In [1]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
%cd drive/My\ Drive/TryTextAttackAgain

/content/drive/My Drive/TryTextAttackAgain


In [3]:
!ls 

BaseLoading.ipynb		      InferSent_snli_pretrained_GLOVE
corpus.py			      multi_nli_train_word_freq.csv
DefendBertGuide.ipynb		      plot_gamma_delta_tuning.ipynb
detect_adversarial.py		      preprocess_datasets
EvalBert.ipynb			      prioritized.py
freq_attacks_mnli.py		      __pycache__
freq_attacks_snli.py		      RunFull
freq_stats.py			      snli_train_word_freq.csv
InferSent.ipynb			      TextAttack
inferSentMultiModel.py		      TrainedBertModels
InferSent_multi_nli_pretrained_GLOVE  TrainNotebooks
inferSentSNLIModel.py		      wandb


In [4]:
#!git clone https://github.com/QData/TextAttack.git

In [5]:
%cd TextAttack/

/content/drive/My Drive/TryTextAttackAgain/TextAttack


In [6]:
!pip install pyarrow>=0.16.0 --force-reinstall
!python3 setup.py install

ERROR: tensorflow 2.3.0 has requirement numpy<1.19.0,>=1.16.0, but you'll have numpy 1.19.1 which is incompatible.
ERROR: datascience 0.10.6 has requirement folium==0.2.1, but you'll have folium 0.8.3 which is incompatible.
ERROR: albumentations 0.1.12 has requirement imgaug<0.2.7,>=0.2.5, but you'll have imgaug 0.2.9 which is incompatible.
ERROR: textattack 0.2.4 has requirement numpy<1.19.0, but you'll have numpy 1.19.1 which is incompatible.
ERROR: flair 0.6 has requirement pytest>=5.3.2, but you'll have pytest 3.6.4 which is incompatible.
running install
running bdist_egg
running egg_info
writing textattack.egg-info/PKG-INFO
writing dependency_links to textattack.egg-info/dependency_links.txt
writing entry points to textattack.egg-info/entry_points.txt
writing requirements to textattack.egg-info/requires.txt
writing top-level names to textattack.egg-info/top_level.txt
writing manifest file 'textattack.egg-info/SOURCES.txt'
installing library code to build/bdist.linux-x86_64/egg
run

In [7]:
!pip list

Package                       Version        
----------------------------- ---------------
absl-py                       0.8.1          
alabaster                     0.7.12         
albumentations                0.1.12         
altair                        4.1.0          
argon2-cffi                   20.1.0         
asgiref                       3.2.10         
astor                         0.8.1          
astropy                       4.0.1.post1    
astunparse                    1.6.3          
atari-py                      0.2.6          
atomicwrites                  1.4.0          
attrs                         20.1.0         
audioread                     2.1.8          
autograd                      1.3            
Babel                         2.8.0          
backcall                      0.2.0          
beautifulsoup4                4.6.3          
bert-score                    0.3.5          
bleach                        3.1.5          
blis                          0.4.

In [8]:
!ls ../

BaseLoading.ipynb		      InferSent_snli_pretrained_GLOVE
corpus.py			      multi_nli_train_word_freq.csv
DefendBertGuide.ipynb		      plot_gamma_delta_tuning.ipynb
detect_adversarial.py		      preprocess_datasets
EvalBert.ipynb			      prioritized.py
freq_attacks_mnli.py		      __pycache__
freq_attacks_snli.py		      RunFull
freq_stats.py			      snli_train_word_freq.csv
InferSent.ipynb			      TextAttack
inferSentMultiModel.py		      TrainedBertModels
InferSent_multi_nli_pretrained_GLOVE  TrainNotebooks
inferSentSNLIModel.py		      wandb


In [9]:
import textattack

wandb: WARNING W&B installed but not logged in.  Run `wandb login` or set the WANDB_API_KEY env variable.


In [10]:
!ls ../TrainedBertModels/bert-base-uncased-multi_nli

1598359875.6866236				   pytorch_model.bin
attack						   README.md
config.json					   special_tokens_map.json
events.out.tfevents.1598359875.f65f0d66daf2.414.0  tokenizer_config.json
log.txt						   train_args.json
matched						   vocab.txt
mismatched


# Evaluating model

### Matched

In [ ]:
!textattack eval --model-from-huggingface  ../TrainedBertModels/bert-base-uncased-multi_nli --dataset-from-nlp multi_nli --num-examples 10000 --dataset_split validation_matched --shuffle False

### MisMatched

In [ ]:
!textattack eval --model-from-huggingface  ../TrainedBertModels/bert-base-uncased-multi_nli --dataset-from-nlp multi_nli --num-examples 10000 --dataset_split validation_mismatched --shuffle False

# Create frequency dictionary

In [11]:
import string
import nltk
import nlp
import csv
import os
import math 
from textattack.shared.utils import words_from_text
import numpy as np

def get_tokenize_sentences(premises,hypothesis):
  all_sentences = []

  for i in zip(premises,hypothesis):
    st = i[0] + " " + i[1]
    tokens = words_from_text(st)
    all_sentences.append(tokens)
  
  return all_sentences

def return_multi_nli_train_dict(dataset):

  train_data = nlp.load_dataset(dataset)['train']

  train_dict = {'premise':[],'hypothesis':[]}

  perc_ = math.ceil(len(train_data)*0.15)
  print("----EVAL DATASET USING : " + str(perc_) + "\n")

  eval_indices = np.sort(np.random.RandomState(21).choice(np.arange(len(train_data)),size=perc_,))
  train_indices = np.delete(np.arange(len(train_data)),eval_indices)

  train_dict['premise'] = np.array(train_data['premise'])[train_indices] 
  train_dict['hypothesis'] = np.array(train_data['hypothesis'])[train_indices]

  return train_dict

def create_freq_corpus(dataset,csvname):


  if dataset is 'multi_nli':
   print('MULTI') 
   train_data = return_multi_nli_train_dict(dataset)

  else:

    train_data = nlp.load_dataset(dataset)['train']

  
  all_sentences = get_tokenize_sentences(train_data['premise'],train_data['hypothesis'])

  freq_dict = {}

  for sentence in all_sentences:
    for token in sentence:
      if token  in freq_dict:
        freq_dict[token] += 1
      else:
        freq_dict[token] = 1 

  print("WRITE")
  with open(csvname, 'w') as csv_file:  
    writer = csv.writer(csv_file)
    for key, value in freq_dict.items():
      writer.writerow([key, value])
  

  return freq_dict

def load_csv(filename):

  with open(filename) as csv_file:
    reader = csv.reader(csv_file)
    freq_dict = dict(reader)
  
  return freq_dict


# Multi

In [12]:
multi_file_name = '../multi_nli_train_word_freq.csv'
multi_dataset_name = 'multi_nli'
#multi_freq_dict = create_freq_corpus(multi_dataset_name,multi_file_name)
multi_freq_dict = load_csv(multi_file_name)

In [13]:
len(multi_freq_dict)

105738

In [14]:
multi_freq_dict['the']

'515381'

# To get frequency statistics

In [15]:
import pandas as pd
from ast import literal_eval
import numpy as np
import math 

def phi_value(freq):
  return math.log(1+freq)

def get_phi_values(words,freq_dict,in_dict=False):

  if in_dict:
    return [phi_value(int(freq_dict[word])) for word in words if word in freq_dict]

  return [phi_value(int(freq_dict[word])) if word in freq_dict else 0 for word in words]


def get_attack_freq_stats(filename,freq_dict):
  
  attack_data = pd.read_csv(filename)

  premises = [i['premise'] for _, i in attack_data.iterrows()] 
  attacked_hypo = [i['attacked_hypothesis'] for _, i in attack_data.iterrows()] 
  original_hypo = [i['original_hypothesis'] for _, i in attack_data.iterrows()] 
  modifiable_indices = [literal_eval(i['modifiable_indices']) for _, i in attack_data.iterrows()] 
  modified_indices = [literal_eval(i['modified_indices']) for _, i in attack_data.iterrows()] 

  attacked_sentences = get_tokenize_sentences(premises,attacked_hypo)
  original_sentences = get_tokenize_sentences(premises,original_hypo)
  
  replaceable_words =[]
  replaced_words = []
  sub_words = []

  for i in range(len(original_sentences)):
    replaceable_words.append(np.array(original_sentences[i])[modifiable_indices[i]])
    replaced_words.append(np.array(original_sentences[i])[modified_indices[i]])
    sub_words.append(np.array(attacked_sentences[i])[modified_indices[i]])

  replaceable_words_freqs = []
  replaced_words_freqs = []
  sub_words_freqs = []
  sub_ovv_freqs = []

  for i in range(len(replaceable_words)):
    replaceable_words_freqs = np.concatenate((replaceable_words_freqs,get_phi_values(replaceable_words[i],freq_dict)))
    replaced_words_freqs = np.concatenate((replaced_words_freqs,get_phi_values(replaced_words[i],freq_dict)))
    sub_words_freqs = np.concatenate((sub_words_freqs,get_phi_values(sub_words[i],freq_dict)))
    sub_ovv_freqs = np.concatenate((sub_ovv_freqs,get_phi_values(sub_words[i],freq_dict, True)))

  print("MEAN:\t" + str(np.mean(replaceable_words_freqs)) + "\t STD:\t" + str(np.std(replaceable_words_freqs)))
  print("MEAN:\t" + str(np.mean(replaced_words_freqs)) + "\t STD:\t" + str(np.std(replaced_words_freqs)))
  print("MEAN:\t" + str(np.mean(sub_words_freqs)) + "\t STD:\t" + str(np.std(sub_words_freqs)))
  print("MEAN:\t" + str(np.mean(sub_ovv_freqs)) + "\t STD:\t" + str(np.std(sub_ovv_freqs)))

In [16]:
!ls ../TrainedBertModels/bert-base-uncased-multi_nli

1598359875.6866236				   pytorch_model.bin
attack						   README.md
config.json					   special_tokens_map.json
events.out.tfevents.1598359875.f65f0d66daf2.414.0  tokenizer_config.json
log.txt						   train_args.json
matched						   vocab.txt
mismatched


# Attacks

##Matched

In [ ]:
!textattack attack --dataset_split validation_matched --attack_output_snli ../TrainedBertModels/bert-base-uncased-multi_nli/matched --recipe random_nli  --num-examples 2000 --dataset-from-nlp multi_nli --model-from-huggingface ../TrainedBertModels/bert-base-uncased-multi_nli

Streaming output truncated to the last 5000 lines.
Premise: Others are Zao (in Tohoku) and a number of resorts in Joshin-etsu Kogen National Park in the Japan Alps, where there are now splendid facilities thanks to the 1998 Winter Olympic Games in Nagano.
Hypothesis: The resorts in the national park are the most exclusive in the country.

Premise: Others are Zao (in Tohoku) and a number of resorts in Joshin-etsu Kogen National Park in the Japan Alps, where there are now splendid facilities thanks to the 1998 Winter Olympic Games in Nagano.
Hypothesis: The resorts Indiana the subject park are the well-nigh sole in the country.


[Succeeded / Failed / Total] 227 / 894 / 1334:  67% 1334/2000 [00:57<00:28, 23.00it/s]--------------------------------------------- Result 1335 ---------------------------------------------
Entailment (84%) --> [SKIPPED]

Premise: One of the city's attractions is the shopping center around the Place Darcy and Rue de la Libert??, where you can hunt for such regio

In [ ]:
get_attack_freq_stats('../TrainedBertModels/bert-base-uncased-multi_nli/matched/attack/random_nli_2000_attacked.csv',multi_freq_dict)

MEAN:	8.583527579944832	 STD:	2.947461297680244
MEAN:	8.041718615791904	 STD:	2.5662240038780464
MEAN:	4.53607927217486	 STD:	2.9904086005204973
MEAN:	5.480463669141032	 STD:	2.3724803398968595


In [ ]:
!textattack attack --dataset_split validation_matched --attack_output_snli ../TrainedBertModels/bert-base-uncased-multi_nli/matched --attack-from-class ../prioritized Priotirized  --num-examples 2000 --dataset-from-nlp multi_nli --model-from-huggingface ../TrainedBertModels/bert-base-uncased-multi_nli

Streaming output truncated to the last 5000 lines.


[Succeeded / Failed / Total] 418 / 730 / 1368:  68% 1368/2000 [02:18<01:04,  9.85it/s]--------------------------------------------- Result 1369 ---------------------------------------------
Entailment (87%) --> Neutral (92%)

Premise: huh-uh i don't even want to go anywhere yeah that's about it
Hypothesis: There is nowhere I want to go.

Premise: huh-uh i don't even want to go anywhere yeah that's about it
Hypothesis: There is nowhere iodine want to go.


[Succeeded / Failed / Total] 419 / 730 / 1369:  68% 1369/2000 [02:18<01:04,  9.85it/s]--------------------------------------------- Result 1370 ---------------------------------------------
Entailment (98%) --> [FAILED]

Premise: Now open political debate flourished, especially in Calcutta where Karl Marx was much appreciated.
Hypothesis: Now political debate flourished in Calcutta especially, where Karl Marx was appreciated.


[Succeeded / Failed / Total] 419 / 731 / 1370:  68% 137

In [ ]:
get_attack_freq_stats('../TrainedBertModels/bert-base-uncased-multi_nli/matched/attack/prioritized_Priotirized_2000_attacked.csv',multi_freq_dict)

MEAN:	8.583527579944832	 STD:	2.947461297680244
MEAN:	8.033733474886326	 STD:	2.53364759635301
MEAN:	3.9513960671112405	 STD:	2.9944861351174614
MEAN:	5.1037625162235605	 STD:	2.3875972388375803


In [ ]:
!textattack attack --recipe textfooler --dataset_split validation_matched --attack_output_snli ../TrainedBertModels/bert-base-uncased-multi_nli/matched  --num-examples 2000 --dataset-from-nlp multi_nli --model-from-huggingface ../TrainedBertModels/bert-base-uncased-multi_nli

Streaming output truncated to the last 5000 lines.

Premise: i know because i think i've been reading i read this ten years ago that they were having these big uh um rallies and people would be in the streets flashing signs statehood yes and other people would statehood down the statehood it's it down there if you're um familiar with their politics they uh it's very uh i i don't know it's called Latino there they have loudspeakers on their cars and they run down the neighborhood saying vote for you know Pierre he's or uh Pedro uh Pedro he's the best it's it's really kind of comical
Hypothesis: I'm not really familiar with the politics there.


[Succeeded / Failed / Total] 1149 / 91 / 1470:  74% 1470/2000 [14:47<05:19,  1.66it/s]--------------------------------------------- Result 1471 ---------------------------------------------
Contradiction (73%) --> Neutral (52%)

Premise: With dark eyes and eyelashes she would have been a beauty. 
Hypothesis: There was nothing that could be done t

In [ ]:
get_attack_freq_stats('../TrainedBertModels/bert-base-uncased-multi_nli/matched/attack/textfooler_2000_attacked.csv',multi_freq_dict)

MEAN:	6.966469069638038	 STD:	2.4575989463603234
MEAN:	6.81341044366641	 STD:	2.0744277034081597
MEAN:	3.7824072191887437	 STD:	2.7667431399200546
MEAN:	4.490858095163778	 STD:	2.43044936244095


In [ ]:
!textattack attack --recipe pwws_snli --dataset_split validation_matched --attack_output_snli ../TrainedBertModels/bert-base-uncased-multi_nli/matched  --num-examples 2000 --dataset-from-nlp multi_nli --model-from-huggingface ../TrainedBertModels/bert-base-uncased-multi_nli

Streaming output truncated to the last 5000 lines.
Contradiction (100%) --> Entailment (81%)

Premise: yeah i know the motor oil
Hypothesis: I know nothing about the motor oil.

Premise: yeah i know the motor oil
Hypothesis: I know zip about the motor oil.


[Succeeded / Failed / Total] 1056 / 174 / 1459:  73% 1459/2000 [15:49<05:52,  1.54it/s]--------------------------------------------- Result 1460 ---------------------------------------------
Neutral (71%) --> Contradiction (49%)

Premise: Paris and its immediate surroundings are a magnet for tourists, students, businessmen, artists, inventors ' in short, everyone except perhaps the farmer and fisherman, who may well come to the city to protest government policies.
Hypothesis: Businessmen spend more time in Paris and its immediate surroundings than inventors do.

Premise: Paris and its immediate surroundings are a magnet for tourists, students, businessmen, artists, inventors ' in short, everyone except perhaps the farmer and fisher

In [ ]:
get_attack_freq_stats('../TrainedBertModels/bert-base-uncased-multi_nli/matched/attack/pwws_snli_2000_attacked.csv',multi_freq_dict)

MEAN:	6.817162309145926	 STD:	2.3648609547811335
MEAN:	6.849046836673239	 STD:	1.9976901694195919
MEAN:	3.686160898178394	 STD:	2.8367195555096707
MEAN:	4.709996917062627	 STD:	2.3366154970248516


In [ ]:
!textattack attack --dataset_split validation_matched --attack_output_snli ../TrainedBertModels/bert-base-uncased-multi_nli/matched --recipe alzantot_gpt2  --num-examples 2000 --dataset-from-nlp multi_nli --model-from-huggingface ../TrainedBertModels/bert-base-uncased-multi_nli/

Streaming output truncated to the last 5000 lines.

Premise: i know that you know the further we go from Adam the worse the food is for you but God still somehow makes us all be able to still live i think it's a miracle we're all still alive after so many generations well the last couple of processed foods you know i mean but i don't know i like to i like to my i like to be able to eat really healthy you know what am saying and i guess i'm going to have to wait for the millennium i think though because i do don't think we're going to restore the earth to you know i think Jesus is the only one that can make this earth be restored to what it should be
Hypothesis: I like to be able to eat real healthy.

Premise: i know that you know the further we go from Adam the worse the food is for you but God still somehow makes us all be able to still live i think it's a miracle we're all still alive after so many generations well the last couple of processed foods you know i mean but i don't know i

In [ ]:
get_attack_freq_stats('../TrainedBertModels/bert-base-uncased-multi_nli/matched/attack/alzantot_gpt2_2000_attacked.csv',multi_freq_dict)

MEAN:	6.817162309145926	 STD:	2.3648609547811335
MEAN:	6.698464430746184	 STD:	1.8564868377889756
MEAN:	3.7723492727605117	 STD:	2.650731368078663
MEAN:	4.535609483674262	 STD:	2.232974430491163


# Frequency Attacks

In [ ]:
!textattack attack --dataset_split validation_matched --attack_output_snli ../TrainedBertModels/bert-base-uncased-multi_nli/matched/ --attack-from-class ../freq_attacks_mnli FrequencyR  --num-examples 2000 --dataset-from-nlp multi_nli --model-from-huggingface ../TrainedBertModels/bert-base-uncased-multi_nli/

Streaming output truncated to the last 5000 lines.
[Succeeded / Failed / Total] 791 / 452 / 1473:  74% 1473/2000 [03:30<01:15,  7.00it/s]Try loading Multi nli training Corpus
--------------------------------------------- Result 1474 ---------------------------------------------
Contradiction (94%) --> [FAILED]

Premise: Even after we hire good people, we need to take steps to retain them.
Hypothesis: Once the hire has already been done, there's no need to do anything different to retain employees.


[Succeeded / Failed / Total] 791 / 453 / 1474:  74% 1474/2000 [03:30<01:15,  7.00it/s]Try loading Multi nli training Corpus
--------------------------------------------- Result 1475 ---------------------------------------------
Neutral (95%) --> Contradiction (98%)

Premise: She hardly needs to mention it--the media bring it up anyway--but she invokes it subtly, alluding (as she did on two Sunday talk shows) to women who drive their daughters halfway across the state to shake my hand, a wom

In [ ]:
get_attack_freq_stats('../TrainedBertModels/bert-base-uncased-multi_nli/matched/attack/freq_attacks_mnli_FrequencyR_2000_attacked.csv',multi_freq_dict)

MEAN:	8.583527579944832	 STD:	2.947461297680244
MEAN:	8.652420303516966	 STD:	2.8269575022199334
MEAN:	0.8181593011685463	 STD:	1.435449601992688
MEAN:	2.5220996469160606	 STD:	1.433297999496027


In [ ]:
!textattack attack --dataset_split validation_matched --attack_output_snli ../TrainedBertModels/bert-base-uncased-multi_nli/matched --attack-from-class ../freq_attacks_mnli FrequencyP  --num-examples 2000 --dataset-from-nlp multi_nli --model-from-huggingface ../TrainedBertModels/bert-base-uncased-multi_nli/

Streaming output truncated to the last 5000 lines.


[Succeeded / Failed / Total] 797 / 450 / 1477:  74% 1477/2000 [03:37<01:17,  6.78it/s]Try loading Multi nli training Corpus
--------------------------------------------- Result 1478 ---------------------------------------------
Contradiction (99%) --> [FAILED]

Premise: because the cold weather was just simply trapped along the ground and couldn't get away
Hypothesis: The weather got away easily.


[Succeeded / Failed / Total] 797 / 451 / 1478:  74% 1478/2000 [03:38<01:17,  6.78it/s]--------------------------------------------- Result 1479 ---------------------------------------------
Neutral (98%) --> [SKIPPED]

Premise: where they they brew their own beer there
Hypothesis: The beer comes from a factory that they purchase it from. 


[Succeeded / Failed / Total] 797 / 451 / 1479:  74% 1479/2000 [03:38<01:16,  6.78it/s]Try loading Multi nli training Corpus
--------------------------------------------- Result 1480 --------------------

In [ ]:
get_attack_freq_stats('../TrainedBertModels/bert-base-uncased-multi_nli/matched/attack/freq_attacks_mnli_FrequencyP_2000_attacked.csv',multi_freq_dict)

MEAN:	8.583527579944832	 STD:	2.947461297680244
MEAN:	8.673412836199445	 STD:	2.8078972283460493
MEAN:	0.8181543614718613	 STD:	1.4590182733685273
MEAN:	2.5966389882726157	 STD:	1.4622052489995059


In [ ]:
!ls ../TrainedBertModels/bert-base-uncased-multi_nli/matched/attack

## Mismatched

In [ ]:
!textattack attack --dataset_split validation_mismatched --attack_output_snli ../TrainedBertModels/bert-base-uncased-multi_nli/mismatched --recipe random_nli  --num-examples 2000 --dataset-from-nlp multi_nli --model-from-huggingface ../TrainedBertModels/bert-base-uncased-multi_nli

In [ ]:
get_attack_freq_stats('../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/attack/random_nli_2000_attacked.csv',multi_freq_dict)

MEAN:	8.395307492722134	 STD:	3.155218896358562
MEAN:	7.791261174780651	 STD:	2.7255794983974133
MEAN:	4.457617275784849	 STD:	2.983554987706261
MEAN:	5.447186442077235	 STD:	2.3425081063942135


In [ ]:
!textattack attack --dataset_split validation_mismatched --attack_output_snli ../TrainedBertModels/bert-base-uncased-multi_nli/mismatched --attack-from-class ../prioritized Priotirized  --num-examples 2000 --dataset-from-nlp multi_nli --model-from-huggingface ../TrainedBertModels/bert-base-uncased-multi_nli

Streaming output truncated to the last 5000 lines.

[Succeeded / Failed / Total] 415 / 740 / 1376:  69% 1376/2000 [02:22<01:04,  9.68it/s]--------------------------------------------- Result 1377 ---------------------------------------------
Contradiction (100%) --> [FAILED]

Premise: And that's why I'm writing to you today.
Hypothesis: And that is why I am never speaking to you again.


[Succeeded / Failed / Total] 415 / 741 / 1377:  69% 1377/2000 [02:22<01:04,  9.68it/s]--------------------------------------------- Result 1378 ---------------------------------------------
Entailment (70%) --> Neutral (83%)

Premise: A small capital in Czechoslovakia 
Hypothesis: Czechoslovakia's compact capital.

Premise: A small capital in Czechoslovakia 
Hypothesis: Czechoslovakia's compact Washington.


[Succeeded / Failed / Total] 416 / 741 / 1378:  69% 1378/2000 [02:22<01:04,  9.68it/s]--------------------------------------------- Result 1379 ---------------------------------------------
Contrad

In [ ]:
get_attack_freq_stats('../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/attack/prioritized_Priotirized_2000_attacked.csv',multi_freq_dict)

MEAN:	8.395307492722134	 STD:	3.155218896358562
MEAN:	7.75306744169596	 STD:	2.7086786289382467
MEAN:	3.908672215231334	 STD:	2.9476936292245655
MEAN:	5.070866172718756	 STD:	2.3192888797906592


In [ ]:
!textattack attack --recipe textfooler --dataset_split validation_mismatched --attack_output_snli ../TrainedBertModels/bert-base-uncased-multi_nli/mismatched  --num-examples 2000 --dataset-from-nlp multi_nli --model-from-huggingface ../TrainedBertModels/bert-base-uncased-multi_nli

Streaming output truncated to the last 5000 lines.
Contradiction (100%) --> Neutral (51%)

Premise: He liked to do little league and soccer with him, and we did all the things families do.
Hypothesis: He has never done sports with him, as families often do.

Premise: He liked to do little league and soccer with him, and we did all the things families do.
Hypothesis: He has never done gym with him, as families consistently do.


[Succeeded / Failed / Total] 1160 / 79 / 1471:  74% 1471/2000 [15:31<05:34,  1.58it/s]--------------------------------------------- Result 1472 ---------------------------------------------
Contradiction (99%) --> Entailment (66%)

Premise: Mihdhar did not trigger the alarm and was permitted through the checkpoint.
Hypothesis: Mihdhar did not make it through the checkpoint.

Premise: Mihdhar did not trigger the alarm and was permitted through the checkpoint.
Hypothesis: Mihdhar did not generate it through the checkpoint.


[Succeeded / Failed / Total] 1161 / 79 

In [ ]:
get_attack_freq_stats('../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/attack/textfooler_2000_attacked.csv',multi_freq_dict)

MEAN:	6.650535459567054	 STD:	2.6515946802231567
MEAN:	6.611123910334863	 STD:	2.2022685607995522
MEAN:	3.6805370952264806	 STD:	2.7373896207310997
MEAN:	4.419226340761024	 STD:	2.3943232362271503


In [ ]:
!textattack attack --recipe pwws_snli --dataset_split validation_mismatched --attack_output_snli ../TrainedBertModels/bert-base-uncased-multi_nli/mismatched  --num-examples 2000 --dataset-from-nlp multi_nli --model-from-huggingface ../TrainedBertModels/bert-base-uncased-multi_nli

Streaming output truncated to the last 5000 lines.


[Succeeded / Failed / Total] 1076 / 153 / 1461:  73% 1461/2000 [17:10<06:20,  1.42it/s]--------------------------------------------- Result 1462 ---------------------------------------------
Entailment (97%) --> Neutral (79%)

Premise:  Yes, I understand.
Hypothesis: I understand that.

Premise:  Yes, I understand.
Hypothesis: I read that.


[Succeeded / Failed / Total] 1077 / 153 / 1462:  73% 1462/2000 [17:10<06:19,  1.42it/s]--------------------------------------------- Result 1463 ---------------------------------------------
Entailment (97%) --> [FAILED]

Premise: There is really no excuse, Fowler says (not he says!)
Hypothesis: There's no excuse.


[Succeeded / Failed / Total] 1077 / 154 / 1463:  73% 1463/2000 [17:10<06:18,  1.42it/s]--------------------------------------------- Result 1464 ---------------------------------------------
Entailment (94%) --> Contradiction (63%)

Premise: The size of the pattern can be changed and 

In [ ]:
get_attack_freq_stats('../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/attack/pwws_snli_2000_attacked.csv',multi_freq_dict)

MEAN:	6.516332643183002	 STD:	2.56049448086248
MEAN:	6.706070233014126	 STD:	2.0919517218248265
MEAN:	3.5252497891268106	 STD:	2.8311273160187085
MEAN:	4.671686458725827	 STD:	2.2948021090678212


In [ ]:
!textattack attack --dataset_split validation_mismatched --attack_output_snli ../TrainedBertModels/bert-base-uncased-multi_nli/mismatched --recipe alzantot_gpt2  --num-examples 2000 --dataset-from-nlp multi_nli --model-from-huggingface ../TrainedBertModels/bert-base-uncased-multi_nli/

Streaming output truncated to the last 5000 lines.
Contradiction (99%) --> Entailment (83%)

Premise: The simplest is for one or more of the members to simply donate one million dollars to the IGGS Scholarship Fund.
Hypothesis: The most complicated is to arrange a donation of one million dollars to the IGGS Scholarship Fund.

Premise: The simplest is for one or more of the members to simply donate one million dollars to the IGGS Scholarship Fund.
Hypothesis: The most complicate is to arranged a donation of one millions dollars to the IGGS Scholarship Fund.


[Succeeded / Failed / Total] 853 / 353 / 1435:  72% 1435/2000 [3:27:13<1:21:35,  8.66s/it]--------------------------------------------- Result 1436 ---------------------------------------------
Neutral (99%) --> [FAILED]

Premise: Societies seldom see what is central in their own cultures, having much less trouble identifying it in the cultures of others.
Hypothesis: This is most common in western societies.


[Succeeded / Failed /

In [ ]:
get_attack_freq_stats('../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/attack/alzantot_gpt2_2000_attacked.csv',multi_freq_dict)

MEAN:	6.516332643183002	 STD:	2.56049448086248
MEAN:	6.4687985220154065	 STD:	2.0000573130347523
MEAN:	3.721959048071843	 STD:	2.5935275822285813
MEAN:	4.4714494317246665	 STD:	2.174757057727242


In [ ]:
ls ../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/attack

alzantot_gpt2_2000_attacked.csv                 pwws_snli_2000_attacked.csv
freq_attacks_mnli_FrequencyP_2000_attacked.csv  random_nli_2000_attacked.csv
freq_attacks_mnli_FrequencyR_2000_attacked.csv  textfooler_2000_attacked.csv
prioritized_Priotirized_2000_attacked.csv


# Frequency Attacks

In [ ]:
!textattack attack --dataset_split validation_mismatched --attack_output_snli ../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/ --attack-from-class ../freq_attacks_mnli FrequencyR  --num-examples 2000 --dataset-from-nlp multi_nli --model-from-huggingface ../TrainedBertModels/bert-base-uncased-multi_nli/

Streaming output truncated to the last 5000 lines.

Premise: One scholar from the fourteenth century from whom Bin Ladin selectively quotes, Ibn Taimiyyah, condemned both corrupt rulers and the clerics who failed to criticize them.
Hypothesis: Bin Ladin quotes the fourteenth century scholar, Ibn Taimiyyah.


[Succeeded / Failed / Total] 798 / 446 / 1476:  74% 1476/2000 [03:44<01:19,  6.58it/s]Try loading Multi nli training Corpus
--------------------------------------------- Result 1477 ---------------------------------------------
Entailment (98%) --> Neutral (72%)

Premise: In the case of the suit manufacturer with plants in different locations, each individual suit is made from shell fabric cut from the same roll and generally the same ply of cloth on the lay table.
Hypothesis: Suit manufacturers may use plants that are based in different places.

Premise: In the case of the suit manufacturer with plants in different locations, each individual suit is made from shell fabric cut from

In [ ]:
get_attack_freq_stats('../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/attack/freq_attacks_mnli_FrequencyR_2000_attacked.csv',multi_freq_dict)

MEAN:	8.395307492722134	 STD:	3.155218896358562
MEAN:	8.532706973726581	 STD:	3.018796296853454
MEAN:	0.850485584245602	 STD:	1.484082707536344
MEAN:	2.608536322149263	 STD:	1.4728829328517112


In [ ]:
!textattack attack --dataset_split validation_mismatched --attack_output_snli ../TrainedBertModels/bert-base-uncased-multi_nli/mismatched --attack-from-class ../freq_attacks_mnli FrequencyP  --num-examples 2000 --dataset-from-nlp multi_nli --model-from-huggingface ../TrainedBertModels/bert-base-uncased-multi_nli/

Streaming output truncated to the last 5000 lines.
Entailment (99%) --> Contradiction (49%)

Premise: Moscow declared it would pull its military forces out of Afghanistan within the next nine months.
Hypothesis: Moscow decided its military forces needed to withdraw from Afghan territory.

Premise: Moscow declared it would pull its military forces out of Afghanistan within the next nine months.
Hypothesis: Mosca decided tsi military hale needed to withdraw from Afghan tierra.


[Succeeded / Failed / Total] 832 / 416 / 1482:  74% 1482/2000 [03:41<01:17,  6.68it/s]Try loading Multi nli training Corpus
--------------------------------------------- Result 1483 ---------------------------------------------
Neutral (71%) --> Contradiction (62%)

Premise: Monsters have had starring roles in SF from its early years.
Hypothesis: Monsters had bit parts in the halcyon days of SF.

Premise: Monsters have had starring roles in SF from its early years.
Hypothesis: Monsters had bit disunite in the hal

In [ ]:
get_attack_freq_stats('../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/attack/freq_attacks_mnli_FrequencyP_2000_attacked.csv',multi_freq_dict)

MEAN:	8.395307492722134	 STD:	3.155218896358562
MEAN:	8.470578369201556	 STD:	3.0089227168850354
MEAN:	0.8246789237818384	 STD:	1.4685511450719553
MEAN:	2.5948318690881482	 STD:	1.480733935117493


In [ ]:
!ls ../TrainedBertModels/bert-base-uncased-multi_nli/matched/attack

alzantot_gpt2_2000_attacked.csv			pwws_snli_2000_attacked.csv
freq_attacks_mnli_FrequencyP_2000_attacked.csv	random_nli_2000_attacked.csv
freq_attacks_mnli_FrequencyR_2000_attacked.csv	textfooler_2000_attacked.csv
prioritized_Priotirized_2000_attacked.csv


In [ ]:
!ls ../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/attack

alzantot_gpt2_2000_attacked.csv			pwws_snli_2000_attacked.csv
freq_attacks_mnli_FrequencyP_2000_attacked.csv	random_nli_2000_attacked.csv
freq_attacks_mnli_FrequencyR_2000_attacked.csv	textfooler_2000_attacked.csv
prioritized_Priotirized_2000_attacked.csv


In [ ]:
!ls ../TrainedBertModels/bert-base-uncased-multi_nli/attack

random_nlieval_whole_attacked.csv


# Defense Models

In [17]:
import argparse
import copy
import importlib
import json
import os
import time
import math 

import textattack

from textattack.commands.attack.attack_args import (
    ATTACK_RECIPE_NAMES,
    BLACK_BOX_TRANSFORMATION_CLASS_NAMES,
    CONSTRAINT_CLASS_NAMES,
    GOAL_FUNCTION_CLASS_NAMES,
    HUGGINGFACE_DATASET_BY_MODEL,
    SEARCH_METHOD_CLASS_NAMES,
    TEXTATTACK_DATASET_BY_MODEL,
    WHITE_BOX_TRANSFORMATION_CLASS_NAMES,
)

# The split token allows users to optionally pass multiple arguments in a single
# parameter by separating them with the split token.
ARGS_SPLIT_TOKEN = "^"

def _cb(s):
  return textattack.shared.utils.color_text(str(s), color="blue", method="ansi")

def phi_value(freq):
    return math.log(1+freq)

def load_module_from_file(file_path):
    """Uses ``importlib`` to dynamically open a file and load an object from
    it."""
    temp_module_name = f"temp_{time.time()}"
    colored_file_path = textattack.shared.utils.color_text(
        file_path, color="blue", method="ansi"
    )
    textattack.shared.logger.info(f"Loading module from `{colored_file_path}`.")
    spec = importlib.util.spec_from_file_location(temp_module_name, file_path)
    module = importlib.util.module_from_spec(spec)
    spec.loader.exec_module(module)
    return module

def parse_model(model_from_file=None, model=None,model_from_huggingface=None,model_batch_size=32):

    if model_from_file:
        # Support loading the model from a .py file where a model wrapper
        # is instantiated.
        colored_model_name = textattack.shared.utils.color_text(
            model_from_file, color="blue", method="ansi"
        )
        textattack.shared.logger.info(
            f"Loading model and tokenizer from file: {colored_model_name}"
        )
        if ARGS_SPLIT_TOKEN in model_from_file:
            model_file, model_name = model_from_file.split(ARGS_SPLIT_TOKEN)
        else:
            _, model_name = model_from_file, "model"
        try:
            model_module = load_module_from_file(model_from_file)
            print("))))HERE(((())))")
            print(model_module)
        except Exception:
            raise ValueError(f"Failed to import file {model_from_file}")
        try:
            model = getattr(model_module, model_name)
        except AttributeError:
            raise AttributeError(
                f"``{model_name}`` not found in module {model_from_file}"
            )

        if not isinstance(model, textattack.models.wrappers.ModelWrapper):
            
            if isinstance(model, textattack.models.NLINet):
                
                model = textattack.models.wrappers.PyTorchModelWrapper(
                    model, model.encoder, batch_size=model_batch_size
                )
                
            else:
                raise TypeError(
                    "Model must be of type "
                    f"``textattack.models.ModelWrapper``, got type {type(model)}"
                )

          
    elif (model in HUGGINGFACE_DATASET_BY_MODEL) or model_from_huggingface:
        # Support loading models automatically from the HuggingFace model hub.
        import transformers

        model_name = (
            HUGGINGFACE_DATASET_BY_MODEL[args.model][0]
            if (model in HUGGINGFACE_DATASET_BY_MODEL)
            else model_from_huggingface
        )

        if ARGS_SPLIT_TOKEN in model_name:
            model_class, model_name = model_name
            model_class = eval(f"transformers.{model_class}")
        else:
            model_class, model_name = (
                transformers.AutoModelForSequenceClassification,
                model_name,
            )
        colored_model_name = textattack.shared.utils.color_text(
            model_name, color="blue", method="ansi"
        )
        textattack.shared.logger.info(
            f"Loading pre-trained model from HuggingFace model repository: {colored_model_name}"
        )
        model = model_class.from_pretrained(model_name)
        tokenizer = textattack.models.tokenizers.AutoTokenizer(model_name)
        model = textattack.models.wrappers.HuggingFaceModelWrapper(
            model, tokenizer, batch_size=model_batch_size
        )
    elif model in TEXTATTACK_DATASET_BY_MODEL:
        # Support loading TextAttack pre-trained models via just a keyword.
        model_path, _ = TEXTATTACK_DATASET_BY_MODEL[model]
        model = textattack.shared.utils.load_textattack_model_from_path(
            model, model_path
        )
        # Choose the approprate model wrapper (based on whether or not this is
        # a HuggingFace model).
        if isinstance(
            model, textattack.models.helpers.BERTForClassification
        ) or isinstance(model, textattack.models.helpers.T5ForTextToText):
            model = textattack.models.wrappers.HuggingFaceModelWrapper(
                model, model.tokenizer, batch_size=model_batch_size
            )
        else:
            model = textattack.models.wrappers.PyTorchModelWrapper(
                model, model.tokenizer, batch_size=model_batch_size
            )
    else:
      raise ValueError("Nothing else supported")
    

    return model

def parse_defense_from_class(defense_from_class=None,freq_dict=None,delta=10,type='discrete',gamma='0.1',candidates=7,model_from_file=None, model=None,model_from_huggingface=None,model_batch_size=32):

    model = parse_model(model_from_file, model,model_from_huggingface,model_batch_size)
    
    if defense_from_class:
      import sys
      path = defense_from_class[0]
      path_class = path.rsplit('/')
      folder_path =  path_class[0] + '/'
      file = path_class[1]

      sys.path.insert(0,folder_path)
      module = importlib.import_module(file)
      my_class = getattr(module, defense_from_class[1])

      return my_class.build(model,freq_dict,delta=delta,type=type,gamma=gamma,candidates=candidates)
    else:
      raise ValueError("currently only attack from class is supported")

In [18]:
import sys
sys.path.insert(0,"../")

In [19]:
import scipy
import torch
import pandas as pd
from collections import deque
import corpus
import tqdm
import time
import textattack

logger = textattack.shared.logger

column_encoder = {"Entailment":0, "Neutral":1, "Contradiction":2}
reversed_encoder = {0:"Entailment", 1:"Neutral", 2:"Contradiction"}

def parse_log_manager():
    # Create logger
    attack_log_manager = textattack.loggers.AttackLogManager()

    '''
    # Get current time for file naming
    timestamp = time.strftime("%Y-%m-%d-%H-%M")

    # Get default directory to save results
    current_dir = os.path.dirname(os.path.realpath(__file__))
    outputs_dir = os.path.join(
        current_dir, os.pardir, os.pardir, os.pardir, "outputs", "attacks"
    )
    out_dir_txt = out_dir_csv = os.path.normpath(outputs_dir)

    # Get default txt and csv file names
    filename_txt = f"_{timestamp}.txt"
    filename_csv = f"_{timestamp}.csv"
    
    

    # in case directory doesn't exist
    if not os.path.exists(out_dir_txt):
        os.makedirs(out_dir_txt)
    if not os.path.exists(out_dir_csv):
        os.makedirs(out_dir_csv)

    attack_log_manager.add_output_file(os.path.join(out_dir_txt, filename_txt))
    '''
    #attack_log_manager.enable_visdom()
    #attack_log_manager.enable_wandb()
    attack_log_manager.enable_stdout()
    return attack_log_manager

def evaluate_set(attacked_dataset,attack,logger=True):

  num_remaining_attacks = len(attacked_dataset)
  worklist = deque(range(0, len(attacked_dataset)))
  start_time = time.time()
  worklist_tail = worklist[-1]

  pbar = tqdm.tqdm(total=num_remaining_attacks, smoothing=0)
  #pbar = tqdm.autonotebook.tqdm(total=num_remaining_attacks)
  attack_log_manager = parse_log_manager()


  num_results = 0
  num_failures = 0
  num_successes = 0

  load_time = time.time()

  probabilities = []
  for result in attack.attack_dataset(attacked_dataset, indices=worklist):

    #or_label = result.original_result.output
    #initial_score = result.original_result.raw_output[or_label]
    #pertubated_score = result.perturbed_result.raw_output[or_label]
    initial_score = 1-result.original_result.score
    pertubated_score = 1-result.perturbed_result.score
    probabilities.append(initial_score-pertubated_score)

    if logger:
      attack_log_manager.log_result(result)

      print("\n")
    pbar.update(1)
    
    num_results += 1

    if (
        type(result) == textattack.attack_results.SuccessfulAttackResult
        or type(result) == textattack.attack_results.MaximizedAttackResult
    ):
        num_successes += 1
    if type(result) == textattack.attack_results.FailedAttackResult:
        num_failures += 1
    
    pbar.set_description(
        "[Succeeded / Failed / Total] {} / {} / {}".format(
            num_successes, num_failures, num_results
        )
    )
    
  pbar.close()

  # Enable summary stdout
  
  if logger:
    attack_log_manager.log_summary()
    attack_log_manager.flush()
  print()
  textattack.shared.logger.info(f"Attack time: {time.time() - load_time}s")

  return num_successes, num_failures, probabilities



class EvalDefenseModel():

  def __init__(
      self,
      defense_from_class,
      model_from_file=None, 
      model=None,
      model_from_huggingface=None,
      model_batch_size=32,
      delta = 10,
      gamma = 1,
      type = 'discrete',
      freq_dict = None,
      data_file = None,
      data_name = "multi_nli",
      candidates = 7,
      logger = True,
      only_attack = False,
      only_original = False,
      #indices_to_modify=None,
      #shifted_idxs=True,
    ):

    # Get attack
    attack = parse_defense_from_class(defense_from_class,freq_dict,delta,type,gamma,candidates,model_from_file, model,model_from_huggingface,model_batch_size)
    
    #Get datasets
    attacked_data = pd.read_csv(data_file,usecols=["premise",'attacked_hypothesis', 'modified_indices' , "attacked_label"],keep_default_na=False)
    original_data = pd.read_csv(data_file,usecols=["premise",'original_hypothesis', "original_label"],keep_default_na=False)
    or_labels = original_data["original_label"]

    to_remove = []
    for index,x in attacked_data.iterrows():
      if x['modified_indices'] == '[]' or or_labels[index]==x['attacked_label']:
        to_remove.append(index)
    attacked_data = attacked_data.drop(to_remove)
    attacked_data = attacked_data.drop(['modified_indices'],axis=1)

    attacked_data["attacked_label"] = [column_encoder[i] for i in attacked_data["attacked_label"] ]


    original_data["original_label"] = [column_encoder[i] for i in original_data["original_label"] ]

    attacked_data = attacked_data.rename(columns={'attacked_hypothesis': 'hypothesis','attacked_label':'label'})
    attacked_dataset = nlp.Dataset.from_pandas(attacked_data)

    attacked_dataset = textattack.datasets.HuggingFaceNlpDataset(
            name=data_name, shuffle=False, split=None, dataset=attacked_dataset, label_map = reversed_encoder)
    
    original_data = original_data.rename(columns={'original_hypothesis': 'hypothesis','original_label':'label'})
    original_dataset = nlp.Dataset.from_pandas(original_data)

    original_dataset = textattack.datasets.HuggingFaceNlpDataset(
            name=data_name, shuffle=False, split=None, dataset=original_dataset, label_map = reversed_encoder)
    
    print("------Attacked Dataset------")
    if not only_original:
      true_positives, false_negatives, pert_probs = evaluate_set(attacked_dataset,attack,logger)
      self.tp = true_positives
      self.fn = false_negatives
      self.adv_probs = pert_probs
      print("True positives :" + str(true_positives) + "\n")
      print("False_negatives :" + str(false_negatives) + "\n")

    if  not only_attack:
      print("------Original Dataset------")
      false_positives, true_negatives, or_probs = evaluate_set(original_dataset,attack,logger)
      print("False positives :" + str(false_positives) + "\n")
      print("True negative :" + str(true_negatives) + "\n")
      self.fp = false_positives
      self.tn = true_negatives
      self.or_probs = or_probs

# Attack whole eval with random

In [20]:
def return_multi_nli_eval_dict(dataset):

  # Get only 20 000 only
  train_data = nlp.load_dataset(dataset)['train']

  valid_dict = {'premise':[],'hypothesis':[]}

  perc_ = math.ceil(len(train_data)*0.15)
  print("----EVAL DATASET USING : " + str(perc_) + "\n")

  eval_indices = np.sort(np.random.RandomState(21).choice(np.arange(len(train_data)),size=perc_,))

  valid_dict['premise'] = np.array(train_data['premise'])[eval_indices[0:20000]] 
  valid_dict['hypothesis'] = np.array(train_data['hypothesis'])[eval_indices[0:20000]]
  valid_dict['label'] = np.array(train_data['label'])[eval_indices[0:20000]]


  return valid_dict

In [21]:
# Create Eval datasets

multi_eval_dataset = return_multi_nli_eval_dict("multi_nli")
len(multi_eval_dataset['label'])

Dataset multi_nli downloaded and prepared to /root/.cache/huggingface/datasets/multi_nli/plain_text/1.0.0/60774175381b9f3f1e6ae1028229e3cdb270d50379f45b9f2c01008f50f09e6b. Subsequent calls will reuse this data.
----EVAL DATASET USING : 58906



20000

In [22]:
from textattack.shared.utils import get_modifiable_indices

def parse_attack_from_recipe(recipe=None,model_from_file=None, model=None,model_from_huggingface=None,model_batch_size=32):

  model = parse_model(model_from_file, model,model_from_huggingface,model_batch_size)

  recipe = eval(f"{ATTACK_RECIPE_NAMES[recipe]}.build(model)")
  recipe.goal_function.query_budget = float("inf")
  recipe.goal_function.model_batch_size = model_batch_size
  recipe.goal_function.model_cache_size = 2 ** 18
  recipe.constraint_cache_size = 2 ** 18
  return recipe
    
def create_snli_dict():
    dictionary = {}
    dictionary["premise"] = []
    dictionary["original_hypothesis"] = []
    dictionary["attacked_hypothesis"] = []
    dictionary["label"] = []
    dictionary["original_label"] = []
    dictionary["attacked_label"] = []
    dictionary['modifiable_indices'] = []
    dictionary['modified_indices'] = []

    return dictionary

def create_csv_file(dictionary,filename):
    df = pd.DataFrame(dictionary)
    df.to_csv(filename, encoding='utf-8', index=False)
    return df

def attack_recipe(recipe,dataset,data_name,folder,model_from_file=None, model=None,model_from_huggingface=None,model_batch_size=32):
     
  # Get attack
  attack = parse_attack_from_recipe(recipe,model_from_file, model,model_from_huggingface,model_batch_size)
    
  #Remove untified instances
  to_remove = []
  for index,x in dataset.iterrows():
    if x['label'] == -1:
      to_remove.append(index)

  dataset = dataset.drop(to_remove)
  dataset = nlp.Dataset.from_pandas(dataset)

  dataset = textattack.datasets.HuggingFaceNlpDataset(
          name=data_name, shuffle=False, split=None, dataset=dataset, label_map = reversed_encoder)
    
  num_remaining_attacks = len(dataset)
  worklist = deque(range(0, len(dataset)))
  start_time = time.time()
  worklist_tail = worklist[-1]

  pbar = tqdm.tqdm(total=num_remaining_attacks, smoothing=0)
  attack_log_manager = parse_log_manager()


  num_results = 0
  num_failures = 0
  num_successes = 0

  load_time = time.time()

  output_attack_dir = os.path.join(folder, "attack")
  output_attack_dir = os.path.normpath(output_attack_dir)
  if not os.path.exists(output_attack_dir):
    os.makedirs(output_attack_dir)

  print("\nAttacks will be saved at " + output_attack_dir + "\n")
  attacked_dict = create_snli_dict()

  for result in attack.attack_dataset(dataset, indices=worklist):

    modifiable_indices = get_modifiable_indices(result.original_result.attacked_text,attack.pre_transformation_constraints)
    prem = result.original_result.attacked_text._text_input['premise']
    hypothesis = result.original_result.attacked_text._text_input['hypothesis']
    attacked_dict['premise'].append(prem)
    attacked_dict['original_hypothesis'].append(hypothesis)
    result.change_word_numbers = len(hypothesis.split())
    attacked_dict['label'].append(result.original_result.ground_truth_output)
    attacked_dict['original_label'].append(result.original_result._processed_output[0])
    attacked_dict['modifiable_indices'].append(list(modifiable_indices))

    if isinstance(result, textattack.attack_results.SkippedAttackResult):
        attacked_dict['attacked_hypothesis'].append(hypothesis)
        attacked_dict['attacked_label'].append(result.original_result._processed_output[0])
        attacked_dict['modified_indices'].append([])

    else:

        hypothesis = result.perturbed_result.attacked_text._text_input['hypothesis']
        attacked_dict['attacked_hypothesis'].append(hypothesis)
        attacked_dict['attacked_label'].append(result.perturbed_result._processed_output[0])
        attacked_dict['modified_indices'].append(list(result.perturbed_result.attacked_text.attack_attrs['modified_indices']))

   
    #attack_log_manager.log_result(result)

    #print("\n")
    pbar.update(1)
    
    num_results += 1

    if (
        type(result) == textattack.attack_results.SuccessfulAttackResult
        or type(result) == textattack.attack_results.MaximizedAttackResult
    ):
        num_successes += 1
    if type(result) == textattack.attack_results.FailedAttackResult:
        num_failures += 1
    pbar.set_description(
        "[Succeeded / Failed / Total] {} / {} / {}".format(
            num_successes, num_failures, num_results
        )
    )

  pbar.close()

  # Enable summary stdout
  
  attack_log_manager.log_summary()
  attack_log_manager.flush()
  print()
  textattack.shared.logger.info(f"Attack time: {time.time() - load_time}s")

  filename = output_attack_dir + "/" + recipe + "eval_whole" 

  create_csv_file(attacked_dict,filename+"_attacked.csv")

In [ ]:
multi_eval_dataset = pd.DataFrame.from_dict(multi_eval_dataset)
classifier = '../TrainedBertModels/bert-base-uncased-multi_nli'
attack_recipe("random_nli",multi_eval_dataset,"multi_nli",classifier,model_from_file=None, model=None,model_from_huggingface=classifier,model_batch_size=32)


#Get prectiles for delta tuning

In [23]:
multi_dataset = nlp.load_dataset("multi_nli")
multi_train_dataset = return_multi_nli_train_dict("multi_nli")
multi_eval_dataset = return_multi_nli_eval_dict("multi_nli")
percentiles = [0,10,20,30,40,50,60,70,80,90,100]

----EVAL DATASET USING : 58906

----EVAL DATASET USING : 58906



In [24]:
# MNLI

frequencies_train = []
for sentence in multi_train_dataset['hypothesis']:
  words = words_from_text(sentence)
  phi_values = get_phi_values(words,multi_freq_dict)
  frequencies_train += phi_values

print("MNLI frequency precentiles")
mnli_precentiles = np.percentile(frequencies_train,percentiles)
print(mnli_precentiles)


MNLI frequency precentiles
[ 0.69314718  4.73619845  6.12905021  7.01301579  7.81883244  8.79270146
  9.81536647 10.5948832  11.3667661  12.44278374 13.15266365]


# Tune delta for discete

In [25]:
!ls 

'=0.16.0'	    docs	 README.md	    textattack
 build		    examples	 requirements.txt   textattack.egg-info
 CONTRIBUTING.md    LICENSE	 setup.cfg	    wandb
 date_now-log.txt   Makefile	 setup.py
 dist		    pytest.ini	 tests


In [26]:
import numpy as np
from sklearn.metrics import roc_auc_score
from sklearn.metrics import f1_score

print('Try loading Mutli training Corpus')
multi_freq_dict = corpus.load_csv('../multi_nli_train_word_freq.csv')

def boostrap_auc(or_probs,adv_probs,times):

  np.random.seed(21)
  labels = np.concatenate((np.ones((len(adv_probs),)),np.zeros((len(adv_probs),))))
  au_scores = np.zeros(times)
  for i in range(times):
    or_sample_probs = np.random.choice(or_probs,len(adv_probs))
    probs = np.concatenate((np.array(adv_probs),np.array(or_sample_probs)))
    au_scores[i] = roc_auc_score(labels,probs)
  
  return np.mean(au_scores)

Try loading Mutli training Corpus


In [ ]:
tps_discrete = []
fns_discrete = []
fps_discrete = []
tns_discrete = []
f1_discrete = []
auc_scores = []

for i in mnli_precentiles:
  print(str(i) + " delta \n")

  stat = EvalDefenseModel(defense_from_class=["../detect_adversarial", "FWGS"],
        model_from_file=None, 
        model=None,
        model_from_huggingface='../TrainedBertModels/bert-base-uncased-multi_nli/',
        model_batch_size=32,
        delta = i,
        type = 'discrete',
        gamma = 1,
        freq_dict = multi_freq_dict,
        data_file='../TrainedBertModels/bert-base-uncased-multi_nli/attack/random_nlieval_whole_attacked.csv',
        data_name = 'multi_nli',
        candidates =7,
        logger = False,
        only_attack = False)
  
  tps_discrete.append(stat.tp)
  fns_discrete.append(stat.fn)
  fps_discrete.append(stat.fp)
  tns_discrete.append(stat.tn)

  true_labels = np.concatenate((np.zeros(stat.tp+stat.fn),np.ones(stat.fp+stat.tn)))
  predictions = np.concatenate((np.zeros(stat.tp),np.ones(stat.fn),np.zeros(stat.fp),np.ones(stat.tn)))
  f1 = f1_score(true_labels, predictions)
  print("F1 score " + str(f1) + '\n')
  f1_discrete.append(f1)
  
  auc_score = boostrap_auc(stat.or_probs,stat.adv_probs,1000)
  print("AUC score " + str(auc_score) + '\n')
  auc_scores.append(auc_score)
  
  

In [ ]:
print("TPS")
print(tps_discrete)
print("\nFNS")
print(fns_discrete)
print("\nFPS")
print(fps_discrete)
print("\nTNS")
print(tns_discrete)
print("\nF1scores")
print(f1_discrete)
print("\nAUCscores")
print(auc_scores)

In [ ]:
discrete_fp_rates = [fp / (fp+tn)  for fp,tn in zip(fps_discrete,tns_discrete)]
print("FPrate")
print(discrete_fp_rates)

discrete_tp_rates = [tp / (tp+fn)  for tp,fn in zip(tps_discrete,fns_discrete)]
print("\nTPrate")
print(discrete_tp_rates)
discrete_max_tp = np.argmax(discrete_tp_rates)
print("Maximum Tprate at delta :")
print(discrete_max_tp)
print("Best delta Value : ")
discrete_delta = mnli_precentiles[discrete_max_tp]
print(discrete_delta)

# Tune gamma (this will be done manually) take the best delta and try values for gamma then check the fpr

In [27]:
discrete_delta = 11.366766102672381

In [28]:
import numpy as np
from sklearn.metrics import roc_auc_score
from sklearn.metrics import f1_score

In [ ]:
import numpy as np
from sklearn.metrics import roc_auc_score
from sklearn.metrics import f1_score

print('Try loading MULTI training Corpus')
multi_freq_dict = corpus.load_csv('../multi_nli_train_word_freq.csv')

tps_discrete = []
fns_discrete = []
fps_discrete = []
tns_discrete = []
f1_discrete = []



for i in [0,0.2,0.4,0.6,0.8,1]:
  print(str(i) + " gamma \n")

  stat = EvalDefenseModel(defense_from_class=["../detect_adversarial", "FWGS"],
        model_from_file=None, 
        model=None,
        model_from_huggingface='../TrainedBertModels/bert-base-uncased-multi_nli',
        model_batch_size=32,
        delta = discrete_delta,
        type = 'continuous',
        gamma = i,
        freq_dict = multi_freq_dict,
        data_file='../TrainedBertModels/bert-base-uncased-multi_nli/attack/random_nlieval_whole_attacked.csv',
        data_name = 'multi_nli',
        candidates =7,
        logger = False,
        only_attack = False,
        only_original=True)
  
  #tps_discrete.append(stat.tp)
  #fns_discrete.append(stat.fn)
  fps_discrete.append(stat.fp)
  tns_discrete.append(stat.tn)

  #true_labels = np.concatenate((np.zeros(stat.tp+stat.fn),np.ones(stat.fp+stat.tn)))
  #predictions = np.concatenate((np.zeros(stat.tp),np.ones(stat.fn),np.zeros(stat.fp),np.ones(stat.tn)))
  #f1 = f1_score(true_labels, predictions)
  #print("F1 score " + str(f1) + '\n')
  #f1_discrete.append(f1)

In [ ]:
import numpy as np
from sklearn.metrics import roc_auc_score
from sklearn.metrics import f1_score

print('Try loading Multi training Corpus')
multi_freq_dict = corpus.load_csv('../multi_nli_train_word_freq.csv')

tps_discrete = []
fns_discrete = []
fps_discrete = []
tns_discrete = []
f1_discrete = []



for i in [0.625,0.65,0.675,0.825,0.85,0.875]:
  print(str(i) + " gamma \n")

  stat = EvalDefenseModel(defense_from_class=["../detect_adversarial", "FWGS"],
        model_from_file=None, 
        model=None,
        model_from_huggingface='../TrainedBertModels/bert-base-uncased-multi_nli/',
        model_batch_size=32,
        delta = discrete_delta,
        type = 'continuous',
        gamma = i,
        freq_dict = multi_freq_dict,
        data_file='../TrainedBertModels/bert-base-uncased-multi_nli/attack/random_nlieval_whole_attacked.csv',
        data_name = 'mutli_nli',
        candidates =7,
        logger = False,
        only_attack = False,
        only_original=True)
  
  #tps_discrete.append(stat.tp)
  #fns_discrete.append(stat.fn)
  fps_discrete.append(stat.fp)
  tns_discrete.append(stat.tn)

  #true_labels = np.concatenate((np.zeros(stat.tp+stat.fn),np.ones(stat.fp+stat.tn)))
  #predictions = np.concatenate((np.zeros(stat.tp),np.ones(stat.fn),np.zeros(stat.fp),np.ones(stat.tn)))
  #f1 = f1_score(true_labels, predictions)
  #print("F1 score " + str(f1) + '\n')
  #f1_discrete.append(f1)

In [29]:
gamma_5 = 0.845
gamma_10 = 0.6375 

# Defened against all attacks

In [ ]:
!ls ../TrainedBertModels/bert-base-uncased-multi_nli/attack

random_nlieval_whole_attacked.csv


In [30]:
attacks = ["random_nli_2000_attacked.csv","prioritized_Priotirized_2000_attacked.csv","textfooler_2000_attacked.csv","pwws_snli_2000_attacked.csv","alzantot_gpt2_2000_attacked.csv"]

## Matched

### Discrete

In [ ]:
tpr_discrete = []
fpr_discrete = []
f1_discrete = []
auc_scores = []


for attack in attacks:
  print("Attack From")
  print(attack)
  print("\n")
  stat = EvalDefenseModel(defense_from_class=["../detect_adversarial", "FWGS"],
        model_from_file=None, 
        model=None,
        model_from_huggingface='../TrainedBertModels/bert-base-uncased-multi_nli/',
        model_batch_size=32,
        delta = discrete_delta,
        type = 'discrete',
        gamma = None,
        freq_dict = multi_freq_dict,
        data_file='../TrainedBertModels/bert-base-uncased-multi_nli/matched/attack/' + attack,
        data_name = 'mutli_nli',
        candidates =7,
        logger = False,
        only_attack = False,
        only_original=False)
    
  tpr_discrete.append(stat.tp/(stat.tp+stat.fn))
  fpr_discrete.append(stat.fp/(stat.fp+stat.tn))

  true_labels = np.concatenate((np.zeros(stat.tp+stat.fn),np.ones(stat.fp+stat.tn)))
  predictions = np.concatenate((np.zeros(stat.tp),np.ones(stat.fn),np.zeros(stat.fp),np.ones(stat.tn)))
  f1 = f1_score(true_labels, predictions)
  print("F1 score " + str(f1) + '\n')
  f1_discrete.append(f1)

  auc_score = boostrap_auc(stat.or_probs,stat.adv_probs,10000)
  print("AUC score " + str(auc_score) + '\n')
  auc_scores.append(auc_score)

textattack: Loading pre-trained model from HuggingFace model repository: ../TrainedBertModels/bert-base-uncased-multi_nli/


Attack From
random_nli_2000_attacked.csv




textattack: Downloading https://textattack.s3.amazonaws.com/word_embeddings/paragramcf.
100%|██████████| 481M/481M [00:09<00:00, 51.8MB/s]
textattack: Unzipping file /root/.cache/textattack/tmpchprsjs2.zip to /root/.cache/textattack/word_embeddings/paragramcf.
textattack: Successfully saved word_embeddings/paragramcf to cache.
textattack: Unknown if model of class <class 'textattack.models.wrappers.huggingface_model_wrapper.HuggingFaceModelWrapper'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


--Detection SEARCH discrete--


textattack: Loading nlp dataset mutli_nli, split None.
textattack: Loading nlp dataset mutli_nli, split None.
  0%|          | 0/332 [00:00<?, ?it/s]

...

------Attacked Dataset------


[Succeeded / Failed / Total] 735 / 447 / 1182: 100%|██████████| 1182/1182 [01:12<00:00, 16.23it/s]
textattack: Attack time: 72.80809473991394s
[Succeeded / Failed / Total] 0 / 2 / 2:   0%|          | 2/2000 [00:00<02:44, 12.15it/s]


True positives :735

False_negatives :447

------Original Dataset------


[Succeeded / Failed / Total] 390 / 1610 / 2000: 100%|██████████| 2000/2000 [02:03<00:00, 16.17it/s]
textattack: Attack time: 123.65245723724365s



False positives :390

True negative :1610

F1 score 0.7936899186591077

AUC score 0.6943776509458001



In [ ]:
print("TPrate")
print(tpr_discrete)
print("\nFPrate")
print(fpr_discrete)
print("\nF1 score")
print(f1_discrete)
print("\n AUC scores")
print(auc_scores)

TPrate
[0.6686746987951807, 0.6341059602649006, 0.6055979643765903, 0.6611570247933884, 0.6218274111675127]

FPrate
[0.195, 0.195, 0.195, 0.195, 0.195]

F1 score
[0.8655913978494625, 0.8405116157661185, 0.7612293144208038, 0.7849829351535836, 0.7936899186591077]

 AUC scores
[0.6704623366961823, 0.7092002953543705, 0.6281553004349332, 0.7241731216181349, 0.6943776509458001]


### Continuous 10%

In [ ]:
tpr_cont10 = []
fpr_cont10 = []
f1_cont10 = []
auc_cont10 = []


for attack in attacks:
  print("Attack From")
  print(attack)
  print("\n")
  stat = EvalDefenseModel(defense_from_class=["../detect_adversarial", "FWGS"],
        model_from_file=None, 
        model=None,
        model_from_huggingface='../TrainedBertModels/bert-base-uncased-multi_nli/',
        model_batch_size=32,
        delta = discrete_delta,
        type = 'continuous',
        gamma = gamma_10,
        freq_dict = multi_freq_dict,
        data_file='../TrainedBertModels/bert-base-uncased-multi_nli/matched/attack/' + attack,
        data_name = 'multi_nli',
        candidates =7,
        logger = False,
        only_attack = False,
        only_original=False)
    
  tpr_cont10.append(stat.tp/(stat.tp+stat.fn))
  fpr_cont10.append(stat.fp/(stat.fp+stat.tn))

  true_labels = np.concatenate((np.zeros(stat.tp+stat.fn),np.ones(stat.fp+stat.tn)))
  predictions = np.concatenate((np.zeros(stat.tp),np.ones(stat.fn),np.zeros(stat.fp),np.ones(stat.tn)))
  f1 = f1_score(true_labels, predictions)
  print("F1 score " + str(f1) + '\n')
  f1_cont10.append(f1)

  auc_score = boostrap_auc(stat.or_probs,stat.adv_probs,10000)
  print("AUC score " + str(auc_score) + '\n')
  auc_cont10.append(auc_score)

textattack: Loading pre-trained model from HuggingFace model repository: ../TrainedBertModels/bert-base-uncased-multi_nli/


Attack From
random_nli_2000_attacked.csv




textattack: Unknown if model of class <class 'textattack.models.wrappers.huggingface_model_wrapper.HuggingFaceModelWrapper'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


--Detection SEARCH continuous--


textattack: Loading nlp dataset multi_nli, split None.
textattack: Loading nlp dataset multi_nli, split None.
[Succeeded / Failed / Total] 1 / 2 / 3:   1%|          | 3/332 [00:00<00:19, 16.92it/s]

...

------Attacked Dataset------


[Succeeded / Failed / Total] 306 / 876 / 1182: 100%|██████████| 1182/1182 [01:13<00:00, 16.17it/s]
textattack: Attack time: 73.09036445617676s
[Succeeded / Failed / Total] 0 / 3 / 3:   0%|          | 3/2000 [00:00<02:04, 16.04it/s]


True positives :306

False_negatives :876

------Original Dataset------


[Succeeded / Failed / Total] 200 / 1800 / 2000: 100%|██████████| 2000/2000 [02:03<00:00, 16.18it/s]
textattack: Attack time: 123.59570026397705s



False positives :200

True negative :1800

F1 score 0.7698887938408897

AUC score 0.6943776509458001



In [ ]:
print("TPrate")
print(tpr_cont10)
print("\nFPrate")
print(fpr_cont10)
print("\nF1 score")
print(f1_cont10)
print("\n AUC scores")
print(auc_cont10)

TPrate
[0.2289156626506024, 0.304635761589404, 0.13486005089058525, 0.3278236914600551, 0.25888324873096447]

FPrate
[0.1, 0.1, 0.1, 0.1, 0.1]

F1 score
[0.8875739644970414, 0.8530805687203792, 0.6976744186046512, 0.7537688442211056, 0.7698887938408897]

 AUC scores
[0.6704623366961823, 0.7092002953543705, 0.6281553004349332, 0.7241731216181349, 0.6943776509458001]


## Continuous 5%

In [ ]:
tpr_cont5 = []
fpr_cont5 = []
f1_cont5 = []
auc_cont5 = []


for attack in attacks:
  print("Attack From")
  print(attack)
  print("\n")
  stat = EvalDefenseModel(defense_from_class=["../detect_adversarial", "FWGS"],
        model_from_file=None, 
        model=None,
        model_from_huggingface='../TrainedBertModels/bert-base-uncased-multi_nli/',
        model_batch_size=32,
        delta = discrete_delta,
        type = 'continuous',
        gamma = gamma_5,
        freq_dict = multi_freq_dict,
        data_file='../TrainedBertModels/bert-base-uncased-multi_nli/matched/attack/' + attack,
        data_name = 'multi_nli',
        candidates =7,
        logger = False,
        only_attack = False,
        only_original=False)
    
  tpr_cont5.append(stat.tp/(stat.tp+stat.fn))
  fpr_cont5.append(stat.fp/(stat.fp+stat.tn))

  true_labels = np.concatenate((np.zeros(stat.tp+stat.fn),np.ones(stat.fp+stat.tn)))
  predictions = np.concatenate((np.zeros(stat.tp),np.ones(stat.fn),np.zeros(stat.fp),np.ones(stat.tn)))
  f1 = f1_score(true_labels, predictions)
  print("F1 score " + str(f1) + '\n')
  f1_cont5.append(f1)

  auc_score = boostrap_auc(stat.or_probs,stat.adv_probs,10000)
  print("AUC score " + str(auc_score) + '\n')
  auc_cont5.append(auc_score)

textattack: Loading pre-trained model from HuggingFace model repository: ../TrainedBertModels/bert-base-uncased-multi_nli/


Attack From
random_nli_2000_attacked.csv




textattack: Unknown if model of class <class 'textattack.models.wrappers.huggingface_model_wrapper.HuggingFaceModelWrapper'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


--Detection SEARCH continuous--


textattack: Loading nlp dataset multi_nli, split None.
textattack: Loading nlp dataset multi_nli, split None.
[Succeeded / Failed / Total] 1 / 2 / 3:   1%|          | 3/332 [00:00<00:18, 17.80it/s]

...

------Attacked Dataset------


[Succeeded / Failed / Total] 121 / 1061 / 1182: 100%|██████████| 1182/1182 [01:12<00:00, 16.27it/s]
textattack: Attack time: 72.6398274898529s
[Succeeded / Failed / Total] 0 / 2 / 2:   0%|          | 2/2000 [00:00<02:37, 12.66it/s]


True positives :121

False_negatives :1061

------Original Dataset------


[Succeeded / Failed / Total] 86 / 1914 / 2000: 100%|██████████| 2000/2000 [02:02<00:00, 16.35it/s]
textattack: Attack time: 122.31043314933777s



False positives :86

True negative :1914

F1 score 0.7694472361809045

AUC score 0.6943776509458001



In [ ]:
print("TPrate")
print(tpr_cont5)
print("\nFPrate")
print(fpr_cont5)
print("\nF1 score")
print(f1_cont5)
print("\n AUC scores")
print(auc_cont5)

TPrate
[0.09337349397590361, 0.1490066225165563, 0.04007633587786259, 0.162534435261708, 0.10236886632825719]

FPrate
[0.043, 0.043, 0.043, 0.043, 0.043]

F1 score
[0.9081850533807829, 0.8644986449864498, 0.7058823529411765, 0.7461988304093568, 0.7694472361809045]

 AUC scores
[0.6704623366961823, 0.7092002953543705, 0.6281553004349332, 0.7241731216181349, 0.6943776509458001]


## MisMatched

### Discrete

In [ ]:
tpr_discrete = []
fpr_discrete = []
f1_discrete = []
auc_scores = []


for attack in attacks:
  print("Attack From")
  print(attack)
  print("\n")
  stat = EvalDefenseModel(defense_from_class=["../detect_adversarial", "FWGS"],
        model_from_file=None, 
        model=None,
        model_from_huggingface='../TrainedBertModels/bert-base-uncased-multi_nli/',
        model_batch_size=32,
        delta = discrete_delta,
        type = 'discrete',
        gamma = None,
        freq_dict = multi_freq_dict,
        data_file='../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/attack/' + attack,
        data_name = 'mutli_nli',
        candidates =7,
        logger = False,
        only_attack = False,
        only_original=False)
    
  tpr_discrete.append(stat.tp/(stat.tp+stat.fn))
  fpr_discrete.append(stat.fp/(stat.fp+stat.tn))

  true_labels = np.concatenate((np.zeros(stat.tp+stat.fn),np.ones(stat.fp+stat.tn)))
  predictions = np.concatenate((np.zeros(stat.tp),np.ones(stat.fn),np.zeros(stat.fp),np.ones(stat.tn)))
  f1 = f1_score(true_labels, predictions)
  print("F1 score " + str(f1) + '\n')
  f1_discrete.append(f1)

  auc_score = boostrap_auc(stat.or_probs,stat.adv_probs,10000)
  print("AUC score " + str(auc_score) + '\n')
  auc_scores.append(auc_score)

textattack: Loading pre-trained model from HuggingFace model repository: ../TrainedBertModels/bert-base-uncased-multi_nli/


Attack From
random_nli_2000_attacked.csv




textattack: Unknown if model of class <class 'textattack.models.wrappers.huggingface_model_wrapper.HuggingFaceModelWrapper'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


--Detection SEARCH discrete--


textattack: Loading nlp dataset mutli_nli, split None.
textattack: Loading nlp dataset mutli_nli, split None.
[Succeeded / Failed / Total] 2 / 1 / 3:   1%|          | 3/339 [00:00<00:22, 15.00it/s]

...

------Attacked Dataset------


[Succeeded / Failed / Total] 723 / 470 / 1193: 100%|██████████| 1193/1193 [01:17<00:00, 15.47it/s]
textattack: Attack time: 77.10357666015625s
[Succeeded / Failed / Total] 1 / 1 / 2:   0%|          | 2/2000 [00:00<02:16, 14.62it/s]


True positives :723

False_negatives :470

------Original Dataset------


[Succeeded / Failed / Total] 412 / 1588 / 2000: 100%|██████████| 2000/2000 [02:11<00:00, 15.21it/s]
textattack: Attack time: 131.48557138442993s



False positives :412

True negative :1588

F1 score 0.7826515524889109

AUC score 0.6914647313646451



In [ ]:
print("TPrate")
print(tpr_discrete)
print("\nFPrate")
print(fpr_discrete)
print("\nF1 score")
print(f1_discrete)
print("\n AUC scores")
print(auc_scores)

TPrate
[0.6607669616519174, 0.632258064516129, 0.6180555555555556, 0.6788370520622042, 0.606035205364627]

FPrate
[0.206, 0.206, 0.206, 0.206, 0.206]

F1 score
[0.8576829597623548, 0.8322851153039832, 0.7574528976866206, 0.7816884075806054, 0.7826515524889109]

 AUC scores
[0.673640931596488, 0.68829303433923, 0.627631922902478, 0.7331366966697616, 0.6914647313646451]


### Continuous 10%

In [ ]:
tpr_cont10 = []
fpr_cont10 = []
f1_cont10 = []
auc_cont10 = []


for attack in attacks:
  print("Attack From")
  print(attack)
  print("\n")
  stat = EvalDefenseModel(defense_from_class=["../detect_adversarial", "FWGS"],
        model_from_file=None, 
        model=None,
        model_from_huggingface='../TrainedBertModels/bert-base-uncased-multi_nli/',
        model_batch_size=32,
        delta = discrete_delta,
        type = 'continuous',
        gamma = gamma_10,
        freq_dict = multi_freq_dict,
        data_file='../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/attack/' + attack,
        data_name = 'multi_nli',
        candidates =7,
        logger = False,
        only_attack = False,
        only_original=False)
    
  tpr_cont10.append(stat.tp/(stat.tp+stat.fn))
  fpr_cont10.append(stat.fp/(stat.fp+stat.tn))

  true_labels = np.concatenate((np.zeros(stat.tp+stat.fn),np.ones(stat.fp+stat.tn)))
  predictions = np.concatenate((np.zeros(stat.tp),np.ones(stat.fn),np.zeros(stat.fp),np.ones(stat.tn)))
  f1 = f1_score(true_labels, predictions)
  print("F1 score " + str(f1) + '\n')
  f1_cont10.append(f1)

  auc_score = boostrap_auc(stat.or_probs,stat.adv_probs,10000)
  print("AUC score " + str(auc_score) + '\n')
  auc_cont10.append(auc_score)

textattack: Loading pre-trained model from HuggingFace model repository: ../TrainedBertModels/bert-base-uncased-multi_nli/


Attack From
random_nli_2000_attacked.csv




textattack: Unknown if model of class <class 'textattack.models.wrappers.huggingface_model_wrapper.HuggingFaceModelWrapper'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


--Detection SEARCH continuous--


textattack: Loading nlp dataset multi_nli, split None.
textattack: Loading nlp dataset multi_nli, split None.
[Succeeded / Failed / Total] 1 / 1 / 2:   1%|          | 2/339 [00:00<00:26, 12.78it/s]

...

------Attacked Dataset------


[Succeeded / Failed / Total] 290 / 903 / 1193: 100%|██████████| 1193/1193 [01:16<00:00, 15.49it/s]
textattack: Attack time: 76.99375867843628s
[Succeeded / Failed / Total] 1 / 1 / 2:   0%|          | 2/2000 [00:00<02:18, 14.46it/s]


True positives :290

False_negatives :903

------Original Dataset------


[Succeeded / Failed / Total] 190 / 1810 / 2000: 100%|██████████| 2000/2000 [02:10<00:00, 15.37it/s]
textattack: Attack time: 130.1299707889557s



False positives :190

True negative :1810

F1 score 0.7680882664969234

AUC score 0.6914647313646451



In [ ]:
print("TPrate")
print(tpr_cont10)
print("\nFPrate")
print(fpr_cont10)
print("\nF1 score")
print(f1_cont10)
print("\n AUC scores")
print(auc_cont10)

TPrate
[0.22713864306784662, 0.27580645161290324, 0.14393939393939395, 0.33198106828938473, 0.24308466051969824]

FPrate
[0.095, 0.095, 0.095, 0.095, 0.095]

F1 score
[0.8889980353634578, 0.849964780464898, 0.7007355787843593, 0.7544810337640684, 0.7680882664969234]

 AUC scores
[0.673640931596488, 0.68829303433923, 0.627631922902478, 0.7331366966697616, 0.6914647313646451]


## Continuous 5%

In [ ]:
tpr_cont5 = []
fpr_cont5 = []
f1_cont5 = []
auc_cont5 = []


for attack in attacks:
  print("Attack From")
  print(attack)
  print("\n")
  stat = EvalDefenseModel(defense_from_class=["../detect_adversarial", "FWGS"],
        model_from_file=None, 
        model=None,
        model_from_huggingface='../TrainedBertModels/bert-base-uncased-multi_nli/',
        model_batch_size=32,
        delta = discrete_delta,
        type = 'continuous',
        gamma = gamma_5,
        freq_dict = multi_freq_dict,
        data_file='../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/attack/' + attack,
        data_name = 'multi_nli',
        candidates =7,
        logger = False,
        only_attack = False,
        only_original=False)
    
  tpr_cont5.append(stat.tp/(stat.tp+stat.fn))
  fpr_cont5.append(stat.fp/(stat.fp+stat.tn))

  true_labels = np.concatenate((np.zeros(stat.tp+stat.fn),np.ones(stat.fp+stat.tn)))
  predictions = np.concatenate((np.zeros(stat.tp),np.ones(stat.fn),np.zeros(stat.fp),np.ones(stat.tn)))
  f1 = f1_score(true_labels, predictions)
  print("F1 score " + str(f1) + '\n')
  f1_cont5.append(f1)

  auc_score = boostrap_auc(stat.or_probs,stat.adv_probs,10000)
  print("AUC score " + str(auc_score) + '\n')
  auc_cont5.append(auc_score)

textattack: Loading pre-trained model from HuggingFace model repository: ../TrainedBertModels/bert-base-uncased-multi_nli/


Attack From
random_nli_2000_attacked.csv




textattack: Unknown if model of class <class 'textattack.models.wrappers.huggingface_model_wrapper.HuggingFaceModelWrapper'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


--Detection SEARCH continuous--


textattack: Loading nlp dataset multi_nli, split None.
textattack: Loading nlp dataset multi_nli, split None.
[Succeeded / Failed / Total] 1 / 2 / 3:   1%|          | 3/339 [00:00<00:20, 16.06it/s]

...

------Attacked Dataset------


[Succeeded / Failed / Total] 123 / 1070 / 1193: 100%|██████████| 1193/1193 [01:16<00:00, 15.52it/s]
textattack: Attack time: 76.86066031455994s
[Succeeded / Failed / Total] 0 / 2 / 2:   0%|          | 2/2000 [00:00<02:17, 14.58it/s]


True positives :123

False_negatives :1070

------Original Dataset------


[Succeeded / Failed / Total] 88 / 1912 / 2000: 100%|██████████| 2000/2000 [02:11<00:00, 15.24it/s]
textattack: Attack time: 131.24805212020874s



False positives :88

True negative :1912

F1 score 0.76756322761943

AUC score 0.6914647313646451



In [ ]:
print("TPrate")
print(tpr_cont5)
print("\nFPrate")
print(fpr_cont5)
print("\nF1 score")
print(f1_cont5)
print("\n AUC scores")
print(auc_cont5)

TPrate
[0.09144542772861357, 0.12903225806451613, 0.03787878787878788, 0.1440162271805274, 0.10310142497904443]

FPrate
[0.044, 0.044, 0.044, 0.044, 0.044]

F1 score
[0.9061611374407582, 0.8589398023360287, 0.7034584253127298, 0.7385090768636539, 0.76756322761943]

 AUC scores
[0.673640931596488, 0.68829303433923, 0.627631922902478, 0.7331366966697616, 0.6914647313646451]


# NWS and FGWS

In [31]:
import scipy
import torch
import pandas as pd
from collections import deque
import corpus
import tqdm
import time
import textattack
from sklearn.metrics import accuracy_score

logger = textattack.shared.logger

                               
column_encoder = {"Entailment":0, "Neutral":1, "Contradiction":2}
reversed_encoder = {0:"Entailment", 1:"Neutral", 2:"Contradiction"}

def parse_log_manager():
    # Create logger
    attack_log_manager = textattack.loggers.AttackLogManager()

    '''
    # Get current time for file naming
    timestamp = time.strftime("%Y-%m-%d-%H-%M")

    # Get default directory to save results
    current_dir = os.path.dirname(os.path.realpath(__file__))
    outputs_dir = os.path.join(
        current_dir, os.pardir, os.pardir, os.pardir, "outputs", "attacks"
    )
    out_dir_txt = out_dir_csv = os.path.normpath(outputs_dir)

    # Get default txt and csv file names
    filename_txt = f"_{timestamp}.txt"
    filename_csv = f"_{timestamp}.csv"
    
    

    # in case directory doesn't exist
    if not os.path.exists(out_dir_txt):
        os.makedirs(out_dir_txt)
    if not os.path.exists(out_dir_csv):
        os.makedirs(out_dir_csv)

    attack_log_manager.add_output_file(os.path.join(out_dir_txt, filename_txt))
    '''
    #attack_log_manager.enable_visdom()
    #attack_log_manager.enable_wandb()
    attack_log_manager.enable_stdout()
    return attack_log_manager

def evaluate_set(attacked_dataset,attack,correct_labels,logger=True):

  num_remaining_attacks = len(attacked_dataset)
  worklist = deque(range(0, len(attacked_dataset)))
  start_time = time.time()
  worklist_tail = worklist[-1]

  pbar = tqdm.tqdm(total=num_remaining_attacks, smoothing=0)
  #pbar = tqdm.autonotebook.tqdm(total=num_remaining_attacks)
  attack_log_manager = parse_log_manager()


  num_results = 0
  num_failures = 0
  num_successes = 0
  transform_labels = []

  load_time = time.time()

  probabilities = []
  for result in attack.attack_dataset(attacked_dataset, indices=worklist):

    #or_label = result.original_result.output
    #initial_score = result.original_result.raw_output[or_label]
    #pertubated_score = result.perturbed_result.raw_output[or_label]
    initial_score = 1-result.original_result.score
    pertubated_score = 1-result.perturbed_result.score
    probabilities.append(initial_score-pertubated_score)
    transform_labels.append(result.perturbed_result.output)

    #if logger:
    #  attack_log_manager.log_result(result)

    #  print("\n")
    pbar.update(1)
    
    num_results += 1

    if (
        type(result) == textattack.attack_results.SuccessfulAttackResult
        or type(result) == textattack.attack_results.MaximizedAttackResult
    ):
        num_successes += 1
    if type(result) == textattack.attack_results.FailedAttackResult:
        num_failures += 1
    
    pbar.set_description(
        "[Succeeded / Failed / Total] {} / {} / {}".format(
            num_successes, num_failures, num_results
        )
    )
    
  pbar.close()

  # Enable summary stdout
  
  if logger:
    attack_log_manager.log_summary()
    attack_log_manager.flush()
  print()
  textattack.shared.logger.info(f"Attack time: {time.time() - load_time}s")

  return num_successes, num_failures, probabilities, transform_labels



class EvalDefenseModel():

  def __init__(
      self,
      defense_from_class,
      model_from_file=None, 
      model=None,
      model_from_huggingface=None,
      model_batch_size=32,
      delta = 10,
      gamma = 1,
      type = 'discrete',
      freq_dict = None,
      data_file = None,
      data_name = "multi_nli",
      candidates = 7,
      logger = True,
      only_attack = False,
      only_original = False,
      #indices_to_modify=None,
      #shifted_idxs=True,
    ):

    # Get attack
    attack = parse_defense_from_class(defense_from_class,freq_dict,delta,type,gamma,candidates,model_from_file, model,model_from_huggingface,model_batch_size)
    
    #Get datasets
    attacked_data = pd.read_csv(data_file,usecols=["premise",'attacked_hypothesis', 'label', 'modified_indices' , "attacked_label"])
    original_data = pd.read_csv(data_file,usecols=["premise",'original_hypothesis', "original_label"])
    or_labels = original_data["original_label"]
    

    to_remove = []
    for index,x in attacked_data.iterrows():
      if x['modified_indices'] == '[]':
        to_remove.append(index)
    attacked_data = attacked_data.drop(to_remove)
    correct_labels = attacked_data['label']
    
    

    attacked_data = attacked_data.drop(['modified_indices','label'],axis=1)

    attacked_data["attacked_label"] = [column_encoder[i] for i in attacked_data["attacked_label"] ]
    # Get original adv accuracy 
    self.adv_acc = accuracy_score(correct_labels,attacked_data["attacked_label"])

    original_data["original_label"] = [column_encoder[i] for i in original_data["original_label"] ]

    attacked_data = attacked_data.rename(columns={'attacked_hypothesis': 'hypothesis','attacked_label':'label'})
    attacked_dataset = nlp.Dataset.from_pandas(attacked_data)

    attacked_dataset = textattack.datasets.HuggingFaceNlpDataset(
            name=data_name, shuffle=False, split=None, dataset=attacked_dataset, label_map = reversed_encoder)
    
    original_data = original_data.rename(columns={'original_hypothesis': 'hypothesis','original_label':'label'})
    original_dataset = nlp.Dataset.from_pandas(original_data)

    original_dataset = textattack.datasets.HuggingFaceNlpDataset(
            name=data_name, shuffle=False, split=None, dataset=original_dataset, label_map = reversed_encoder)
    
    print("------Attacked Dataset------")
    if not only_original:
      true_positives, false_negatives, pert_probs, transform_labels = evaluate_set(attacked_dataset,attack,logger)
      self.tp = true_positives
      self.fn = false_negatives
      self.adv_probs = pert_probs

      print("True positives :" + str(true_positives) + "\n")
      print("False_negatives :" + str(false_negatives) + "\n")

      # Get transformed adv accuracy 
      self.transform_acc = accuracy_score(correct_labels,transform_labels)

    if  not only_attack:
      print("------Original Dataset------")
      false_positives, true_negatives, or_probs, _i10 = evaluate_set(original_dataset,attack,logger)
      print("False positives :" + str(false_positives) + "\n")
      print("True negative :" + str(true_negatives) + "\n")
      self.fp = false_positives
      self.tn = true_negatives
      self.or_probs = or_probs

#Matched

In [32]:
tpr_nws = []
fpr_nws = []
f1_nws = []
auc_nws = []
adv_acc_nws = []
tr_acc_nws =[]


for attack in attacks:
  print("Attack From")
  print(attack)
  print("\n")
  stat = EvalDefenseModel(defense_from_class=["../detect_adversarial", "NWS"],
        model_from_file=None, 
        model=None,
        model_from_huggingface='../TrainedBertModels/bert-base-uncased-multi_nli/',
        model_batch_size=32,
        delta = None,
        type = None,
        gamma = None,
        freq_dict = multi_freq_dict,
        data_file='../TrainedBertModels/bert-base-uncased-multi_nli/matched/attack/' + attack,
        data_name = 'mutli_nli',
        candidates =7,
        logger = False,
        only_attack = False,
        only_original=False)
    
  tpr_nws.append(stat.tp/(stat.tp+stat.fn))
  fpr_nws.append(stat.fp/(stat.fp+stat.tn))

  true_labels = np.concatenate((np.zeros(stat.tp+stat.fn),np.ones(stat.fp+stat.tn)))
  predictions = np.concatenate((np.zeros(stat.tp),np.ones(stat.fn),np.zeros(stat.fp),np.ones(stat.tn)))
  f1 = f1_score(true_labels, predictions)
  print("F1 score " + str(f1) + '\n')
  f1_nws.append(f1)

  auc_score = boostrap_auc(stat.or_probs,stat.adv_probs,10000)
  print("AUC score " + str(auc_score) + '\n')
  auc_nws.append(auc_score)

  adv_acc_nws.append(stat.adv_acc) 
  tr_acc_nws.append(stat.transform_acc)
  print("Adversarial Acc " + str(stat.adv_acc))
  print("Transform Acc " + str(stat.transform_acc))


textattack: Loading pre-trained model from HuggingFace model repository: ../TrainedBertModels/bert-base-uncased-multi_nli/


Attack From
random_nli_2000_attacked.csv




textattack: Downloading https://textattack.s3.amazonaws.com/word_embeddings/paragramcf.
100%|██████████| 481M/481M [00:37<00:00, 13.0MB/s]
textattack: Unzipping file /root/.cache/textattack/tmp6k5y8_by.zip to /root/.cache/textattack/word_embeddings/paragramcf.
textattack: Successfully saved word_embeddings/paragramcf to cache.
textattack: Unknown if model of class <class 'textattack.models.wrappers.huggingface_model_wrapper.HuggingFaceModelWrapper'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


-- Vocabulary SEARCH --


textattack: Loading nlp dataset mutli_nli, split None.
textattack: Loading nlp dataset mutli_nli, split None.
[Succeeded / Failed / Total] 0 / 1 / 1:   0%|          | 1/1182 [00:00<02:31,  7.77it/s]

...

------Attacked Dataset------


[Succeeded / Failed / Total] 181 / 1497 / 1678: 100%|██████████| 1678/1678 [00:31<00:00, 54.11it/s]
textattack: Attack time: 31.01211380958557s
[Succeeded / Failed / Total] 1 / 11 / 12:   1%|          | 12/2000 [00:00<00:30, 65.51it/s]


True positives :181

False_negatives :1497

------Original Dataset------


[Succeeded / Failed / Total] 5 / 1995 / 2000: 100%|██████████| 2000/2000 [00:28<00:00, 69.02it/s]
textattack: Attack time: 28.978565216064453s



False positives :5

True negative :1995

F1 score 0.7265112891478515

AUC score 0.5313520845201377

Adversarial Acc 0.29558998808104886
Transform Acc 0.3831942789034565


In [33]:
print("TP rates")
print(tpr_nws)
print("\nFP rates")
print(fpr_nws)
print("\nF1 scores")
print(f1_nws)
print("\nAuc scores")
print(auc_nws)
print("\nAdv_acc")
print(adv_acc_nws)
print("\nTransform_acc")
print(tr_acc_nws)

TP rates
[0.09560067681895093, 0.13189897100093545, 0.12374185908821789, 0.1592128801431127, 0.10786650774731824]

FP rates
[0.0045, 0.004, 0.0045, 0.0005, 0.0025]

F1 scores
[0.7869565217391304, 0.8097560975609757, 0.7278376896362639, 0.739138472915511, 0.7265112891478515]

Auc scores
[0.5153486030588552, 0.52999458626957, 0.5554552119187259, 0.5685410005372772, 0.5313520845201377]

Adv_acc
[0.7191201353637902, 0.43498596819457436, 0.06927175843694494, 0.13416815742397137, 0.29558998808104886]

Transform_acc
[0.7876480541455161, 0.5575304022450889, 0.1876850207223209, 0.28920691711389385, 0.3831942789034565]


In [34]:
tpr_fgws = []
fpr_fgws = []
f1_fgws = []
auc_fgws = []
adv_acc_fgws = []
tr_acc_fgws = []

for attack in attacks:
  print("Attack From")
  print(attack)
  print("\n")
  stat = EvalDefenseModel(defense_from_class=["../detect_adversarial", "FWGS"],
        model_from_file=None, 
        model=None,
        model_from_huggingface='../TrainedBertModels/bert-base-uncased-multi_nli/',
        model_batch_size=32,
        delta = discrete_delta,
        type = 'discrete',
        gamma = None,
        freq_dict = multi_freq_dict,
        data_file='../TrainedBertModels/bert-base-uncased-multi_nli/matched/attack/' + attack,
        data_name = 'multi_nli',
        candidates =7,
        logger = False,
        only_attack = False,
        only_original=False)
    
  tpr_fgws.append(stat.tp/(stat.tp+stat.fn))
  fpr_fgws.append(stat.fp/(stat.fp+stat.tn))

  true_labels = np.concatenate((np.zeros(stat.tp+stat.fn),np.ones(stat.fp+stat.tn)))
  predictions = np.concatenate((np.zeros(stat.tp),np.ones(stat.fn),np.zeros(stat.fp),np.ones(stat.tn)))
  f1 = f1_score(true_labels, predictions)
  print("F1 score " + str(f1) + '\n')
  f1_fgws.append(f1)

  auc_score = boostrap_auc(stat.or_probs,stat.adv_probs,10000)
  print("AUC score " + str(auc_score) + '\n')
  auc_fgws.append(auc_score)
  
  adv_acc_fgws.append(stat.adv_acc) 
  tr_acc_fgws.append(stat.transform_acc)
  print("Adversarial Acc " + str(stat.adv_acc))
  print("Transform Acc " + str(stat.transform_acc))

textattack: Loading pre-trained model from HuggingFace model repository: ../TrainedBertModels/bert-base-uncased-multi_nli/


Attack From
random_nli_2000_attacked.csv




textattack: Unknown if model of class <class 'textattack.models.wrappers.huggingface_model_wrapper.HuggingFaceModelWrapper'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Loading nlp dataset multi_nli, split None.


--Detection SEARCH discrete--


textattack: Loading nlp dataset multi_nli, split None.
[Succeeded / Failed / Total] 2 / 2 / 4:   0%|          | 4/1182 [00:00<00:42, 27.80it/s]

...

------Attacked Dataset------


[Succeeded / Failed / Total] 776 / 902 / 1678: 100%|██████████| 1678/1678 [01:15<00:00, 22.19it/s]
textattack: Attack time: 75.6273901462555s
[Succeeded / Failed / Total] 1 / 3 / 4:   0%|          | 4/2000 [00:00<01:32, 21.67it/s]


True positives :776

False_negatives :902

------Original Dataset------


[Succeeded / Failed / Total] 393 / 1607 / 2000: 100%|██████████| 2000/2000 [01:31<00:00, 21.76it/s]
textattack: Attack time: 91.89236044883728s



False positives :393

True negative :1607

F1 score 0.7127966289642936

AUC score 0.5596008636267422

Adversarial Acc 0.29558998808104886
Transform Acc 0.6644815256257449


In [35]:
print("TP rates")
print(tpr_fgws)
print("\nFP rates")
print(fpr_fgws)
print("\nF1 scores")
print(f1_fgws)
print("\nAuc scores")
print(auc_fgws)
print("\nAdv_acc")
print(adv_acc_fgws)
print("\nTransform_acc")
print(tr_acc_fgws)

TP rates
[0.2800338409475465, 0.41814780168381666, 0.5695677915926584, 0.5807990459153249, 0.46245530393325385]

FP rates
[0.1965, 0.1965, 0.1965, 0.1965, 0.1965]

F1 scores
[0.7209510991475998, 0.7599905414991722, 0.7415782187355792, 0.7457076566125289, 0.7127966289642936]

Auc scores
[0.48014434935624895, 0.5362033639579931, 0.5932682302615644, 0.6568983263693543, 0.5596008636267422]

Adv_acc
[0.7191201353637902, 0.43498596819457436, 0.06927175843694494, 0.13416815742397137, 0.29558998808104886]

Transform_acc
[0.7580372250423012, 0.7034611786716558, 0.5713439905269391, 0.6463923673225999, 0.6644815256257449]


#Mismatched

In [36]:
tpr_nws = []
fpr_nws = []
f1_nws = []
auc_nws = []
adv_acc_nws = []
tr_acc_nws =[]


for attack in attacks:
  print("Attack From")
  print(attack)
  print("\n")
  stat = EvalDefenseModel(defense_from_class=["../detect_adversarial", "NWS"],
        model_from_file=None, 
        model=None,
        model_from_huggingface='../TrainedBertModels/bert-base-uncased-multi_nli/',
        model_batch_size=32,
        delta = None,
        type = None,
        gamma = None,
        freq_dict = multi_freq_dict,
        data_file='../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/attack/' + attack,
        data_name = 'mutli_nli',
        candidates =7,
        logger = False,
        only_attack = False,
        only_original=False)
    
  tpr_nws.append(stat.tp/(stat.tp+stat.fn))
  fpr_nws.append(stat.fp/(stat.fp+stat.tn))

  true_labels = np.concatenate((np.zeros(stat.tp+stat.fn),np.ones(stat.fp+stat.tn)))
  predictions = np.concatenate((np.zeros(stat.tp),np.ones(stat.fn),np.zeros(stat.fp),np.ones(stat.tn)))
  f1 = f1_score(true_labels, predictions)
  print("F1 score " + str(f1) + '\n')
  f1_nws.append(f1)

  auc_score = boostrap_auc(stat.or_probs,stat.adv_probs,10000)
  print("AUC score " + str(auc_score) + '\n')
  auc_nws.append(auc_score)

  adv_acc_nws.append(stat.adv_acc) 
  tr_acc_nws.append(stat.transform_acc)
  print("Adversarial Acc " + str(stat.adv_acc))
  print("Transform Acc " + str(stat.transform_acc))


textattack: Loading pre-trained model from HuggingFace model repository: ../TrainedBertModels/bert-base-uncased-multi_nli/


Attack From
random_nli_2000_attacked.csv




textattack: Unknown if model of class <class 'textattack.models.wrappers.huggingface_model_wrapper.HuggingFaceModelWrapper'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.


-- Vocabulary SEARCH --


textattack: Loading nlp dataset mutli_nli, split None.
textattack: Loading nlp dataset mutli_nli, split None.
[Succeeded / Failed / Total] 0 / 10 / 10:   1%|          | 10/1212 [00:00<00:23, 51.89it/s]

...

------Attacked Dataset------


[Succeeded / Failed / Total] 189 / 1486 / 1675: 100%|██████████| 1675/1675 [00:31<00:00, 53.94it/s]
textattack: Attack time: 31.054049968719482s
[Succeeded / Failed / Total] 0 / 13 / 13:   1%|          | 13/2000 [00:00<00:29, 66.46it/s]


True positives :189

False_negatives :1486

------Original Dataset------


[Succeeded / Failed / Total] 22 / 1978 / 2000: 100%|██████████| 2000/2000 [00:29<00:00, 66.71it/s]
textattack: Attack time: 29.981816053390503s



False positives :22

True negative :1978

F1 score 0.7240117130307467

AUC score 0.5320037613722433

Adversarial Acc 0.28776119402985073
Transform Acc 0.37970149253731345


In [37]:
print("TP rates")
print(tpr_nws)
print("\nFP rates")
print(fpr_nws)
print("\nF1 scores")
print(f1_nws)
print("\nAuc scores")
print(auc_nws)
print("\nAdv_acc")
print(adv_acc_nws)
print("\nTransform_acc")
print(tr_acc_nws)

TP rates
[0.08993399339933994, 0.12839737582005623, 0.1362559241706161, 0.18835412953060013, 0.11283582089552238]

FP rates
[0.0085, 0.011, 0.0085, 0.0115, 0.011]

F1 scores
[0.7797876523790798, 0.8060309698451509, 0.7289101268149237, 0.7400336889387985, 0.7240117130307467]

Auc scores
[0.5097976698226754, 0.5200718422400218, 0.5502465229540553, 0.586377693293778, 0.5320037613722433]

Adv_acc
[0.7202970297029703, 0.4189315838800375, 0.061611374407582936, 0.12121212121212122, 0.28776119402985073]

Transform_acc
[0.7673267326732673, 0.5360824742268041, 0.18838862559241706, 0.30005941770647654, 0.37970149253731345]


In [38]:
tpr_fgws = []
fpr_fgws = []
f1_fgws = []
auc_fgws = []
adv_acc_fgws = []
tr_acc_fgws = []

for attack in attacks:
  print("Attack From")
  print(attack)
  print("\n")
  stat = EvalDefenseModel(defense_from_class=["../detect_adversarial", "FWGS"],
        model_from_file=None, 
        model=None,
        model_from_huggingface='../TrainedBertModels/bert-base-uncased-multi_nli/',
        model_batch_size=32,
        delta = discrete_delta,
        type = 'discrete',
        gamma = None,
        freq_dict = multi_freq_dict,
        data_file='../TrainedBertModels/bert-base-uncased-multi_nli/mismatched/attack/' + attack,
        data_name = 'multi_nli',
        candidates =7,
        logger = False,
        only_attack = False,
        only_original=False)
    
  tpr_fgws.append(stat.tp/(stat.tp+stat.fn))
  fpr_fgws.append(stat.fp/(stat.fp+stat.tn))

  true_labels = np.concatenate((np.zeros(stat.tp+stat.fn),np.ones(stat.fp+stat.tn)))
  predictions = np.concatenate((np.zeros(stat.tp),np.ones(stat.fn),np.zeros(stat.fp),np.ones(stat.tn)))
  f1 = f1_score(true_labels, predictions)
  print("F1 score " + str(f1) + '\n')
  f1_fgws.append(f1)

  auc_score = boostrap_auc(stat.or_probs,stat.adv_probs,10000)
  print("AUC score " + str(auc_score) + '\n')
  auc_fgws.append(auc_score)
  
  adv_acc_fgws.append(stat.adv_acc) 
  tr_acc_fgws.append(stat.transform_acc)
  print("Adversarial Acc " + str(stat.adv_acc))
  print("Transform Acc " + str(stat.transform_acc))

textattack: Loading pre-trained model from HuggingFace model repository: ../TrainedBertModels/bert-base-uncased-multi_nli/


Attack From
random_nli_2000_attacked.csv




textattack: Unknown if model of class <class 'textattack.models.wrappers.huggingface_model_wrapper.HuggingFaceModelWrapper'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Loading nlp dataset multi_nli, split None.


--Detection SEARCH discrete--


textattack: Loading nlp dataset multi_nli, split None.
[Succeeded / Failed / Total] 1 / 3 / 4:   0%|          | 4/1212 [00:00<00:58, 20.61it/s]

...

------Attacked Dataset------


[Succeeded / Failed / Total] 772 / 903 / 1675: 100%|██████████| 1675/1675 [01:19<00:00, 21.09it/s]
textattack: Attack time: 79.40874481201172s
[Succeeded / Failed / Total] 2 / 2 / 4:   0%|          | 4/2000 [00:00<01:34, 21.04it/s]


True positives :772

False_negatives :903

------Original Dataset------


[Succeeded / Failed / Total] 414 / 1586 / 2000: 100%|██████████| 2000/2000 [01:37<00:00, 20.55it/s]
textattack: Attack time: 97.33042550086975s



False positives :414

True negative :1586

F1 score 0.7066161728670082

AUC score 0.5516632271953664

Adversarial Acc 0.28776119402985073
Transform Acc 0.635223880597015


In [41]:
print("TP rates")
print(tpr_fgws)
print("\nFP rates")
print(fpr_fgws)
print("\nF1 scores")
print(f1_fgws)
print("\nAuc scores")
print(auc_fgws)
print("\nAdv_acc")
print(adv_acc_fgws)
print("\nTransform_acc")
print(tr_acc_fgws)

TP rates
[0.28795379537953797, 0.4442361761949391, 0.5859004739336493, 0.6096256684491979, 0.4608955223880597]

FP rates
[0.207, 0.207, 0.207, 0.207, 0.207]

F1 scores
[0.7129692065632726, 0.7590332615458243, 0.7402567094515753, 0.7475842564223427, 0.7066161728670082]

Auc scores
[0.4832548435474736, 0.5434974142042654, 0.6008435975964994, 0.6646503754118728, 0.5516632271953664]

Adv_acc
[0.7202970297029703, 0.4189315838800375, 0.061611374407582936, 0.12121212121212122, 0.28776119402985073]

Transform_acc
[0.7772277227722773, 0.676663542642924, 0.5758293838862559, 0.6702317290552585, 0.635223880597015]
